In [1]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# ========== python ==========
import os
from pathlib import Path
from logging import Logger
from typing import List, Dict, Tuple, Optional, Union, Callable, Final, Literal, get_args
from operator import itemgetter, attrgetter
import itertools
from IPython.display import display

from utils.setup import setup_logger, get_device
from const.const_values import PROJECT_DIR

os.chdir(PROJECT_DIR)
logger: Logger = setup_logger(__name__, f'{PROJECT_DIR}/log/jupyter_run.log')
device = get_device(device_name='cpu', logger=logger)

In [2]:
# jupyter
import seaborn as sns
import matplotlib.pyplot as plt
# Machine learning
import numpy as np
import pandas as pd
import h5py
import optuna
# torch
import torch
from torch.nn import CrossEntropyLoss
from torch.utils.data import Dataset
from torch.utils.data.dataloader import DataLoader
from torch.utils.tensorboard.writer import SummaryWriter
# torch ignite
from ignite.engine import Engine
from ignite.handlers import Checkpoint
# My items
from models.datasets.data_helper import MyDataHelper, MyDataLoaderHelper, DefaultTokens
from models.datasets.datasets_for_story import StoryTriple
# My utils
from utils.setup import load_param
from utils.torch import load_model, torch_fix_seed
# main function
from run_for_KGC import main_function

In [3]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 100)

In [4]:
from const.const_values import CPU, MODEL
from models.KGModel.kg_model import HEAD, RELATION, TAIL
from utils.torch_ignite import TRAINER, EVALUATOR
from const.const_values import DATASETS, DATA_HELPER, DATA_LOADERS, TRAIN_RETURNS

In [5]:
SEED: Final[int] = 42
args_path = f'{PROJECT_DIR}/models/kgc03/all100/param.pkl'
model_path = f'{PROJECT_DIR}/models/kgc03/all100/model.pth'

In [6]:
args = load_param(args_path)

# args.pre_train = True
args.logger = logger
args.device = device
args.batch_size = 1
args.pre_train=False
args.init_embedding_using_bert = False
args.model_path = model_path
args.only_load_trainer_evaluator = True
# args.old_data = 1

del args.optuna_file, args.device_name, args.pid, args.study_name, args.n_trials

### ↑ import and setting const value complete.  ↑

In [7]:
args

Namespace(notebook=False, console_level='info', logfile='models/kgc03/all100/log.log', param_file='models/kgc03/all100/param.pkl', train_anyway=False, old_data=0, tensorboard_dir='models/kgc03/all100/tensorboard', checkpoint_dir='models/kgc03/all100/checkpoint/', model_path='/Users/ryoyakaneda/Documents/学校/M1Study/knowledge_graph/models/kgc03/all100/model.pth', resume_from_checkpoint=False, resume_from_last_point=False, only_load_trainer_evaluator=True, resume_checkpoint_path=None, pre_train=False, train_valid_test=False, only_train=True, use_for_challenge100=False, use_for_challenge090=False, use_for_challenge075=False, use_title=None, do_optuna=False, story_special_num=5, relation_special_num=5, entity_special_num=5, padding_token_e=0, cls_token_e=1, mask_token_e=2, sep_token_e=3, bos_token_e=4, padding_token_r=0, cls_token_r=1, mask_token_r=2, sep_token_r=3, bos_token_r=4, padding_token_s=0, cls_token_s=1, mask_token_s=2, sep_token_s=3, bos_token_s=4, model_version='03', embedding_d

These are the parameters related to the model.

In [8]:
"embedding_dim={}, entity_embedding_dim={}, relation_embedding_dim={}, nhead={}, num_layers={}, ".format(
    args.embedding_dim, args.entity_embedding_dim, args.relation_embedding_dim, args.nhead, args.num_layers,)

'embedding_dim=128, entity_embedding_dim=128, relation_embedding_dim=64, nhead=4, num_layers=4, '

### First, the model is initialized and then overwritten with a previously saved model.
### Training data is made at the same time.

In [9]:
torch_fix_seed(seed=SEED)
return_dict = main_function(args, logger=logger)

2023-02-04 06:55:12 - INFO - run_for_KGC.py - 893 - ----- make datahelper start. -----
2023-02-04 06:55:12 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-04 06:55:12 - INFO - data_helper.py - 334 - entity num: 7812
2023-02-04 06:55:12 - INFO - data_helper.py - 335 - relation num: 62
2023-02-04 06:55:12 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-04 06:55:12 - INFO - data_helper.py - 607 - ========== Show DataHelper ==========
2023-02-04 06:55:12 - INFO - data_helper.py - 333 - ====== Show MyRawData ======
2023-02-04 06:55:12 - INFO - data_helper.py - 334 - entity num: 7812
2023-02-04 06:55:12 - INFO - data_helper.py - 335 - relation num: 62
2023-02-04 06:55:12 - INFO - data_helper.py - 336 - ====== Show MyRawData ======
2023-02-04 06:55:12 - INFO - data_helper.py - 609 - entity_special_dicts: {0: '<pad_e>', 1: '<cls_e>', 2: '<mask_e>', 3: '<sep_e>', 4: '<bos_e>'}
2023-02-04 06:55:12 - INFO - data_helper.py - 610 - relation_special_dicts: {

In [10]:
model = return_dict[MODEL]

dataset_train: StoryTriple = return_dict[DATASETS][0]
triple: torch.Tensor = dataset_train.triple
data_helper: MyDataHelper = return_dict[DATA_HELPER]
evaluator: Checkpoint = return_dict[TRAIN_RETURNS][EVALUATOR]

load_model(model, args.model_path, device)
model.eval()

entities, relations = data_helper.processed_entities, data_helper.processed_relations
d_e, d_r = {e: i for i, e in enumerate(entities)}, {r: i for i, r in enumerate(relations)}

triple_df = pd.DataFrame([(entities[_t[0]], relations[_t[1]], entities[_t[2]]) for _t in triple], columns=[HEAD, RELATION, TAIL])
story_entities = triple_df[HEAD].tolist()

### One of the inputs is shown as an example.

### The sequence contains triples from the beginning of each scene to the specified length. In this case, the length is set to 512.

In [12]:
print("training sequence shape:", dataset_train[0].shape)
dataset_train[0]

training sequence shape: torch.Size([512, 3])


tensor([[   4,    4,    4],
        [3958,    6,    5],
        [3958,   21, 7356],
        ...,
        [4046,   44,  510],
        [   4,    4,    4],
        [4047,    6,   14]])

#### Note that the data presented in the previous section are part of this series below.

In [13]:
triple_df[triple_df['head'].str.contains('ResidentPatient')]

head          relation                          tail
11169   ResidentPatient:001       kgc:subject               AllTitle:Holmes
11170   ResidentPatient:001  kgc:hasPredicate          word.predicate:guess
11171   ResidentPatient:001          kgc:what           ResidentPatient:002
11172   ResidentPatient:001          kgc:what           ResidentPatient:003
11173   ResidentPatient:001          kgc:what           ResidentPatient:004
...                     ...               ...                           ...
12898   ResidentPatient:324   kgc:hasProperty           word.predicate:want
12899   ResidentPatient:324          kgc:what          ResidentPatient:324a
12901  ResidentPatient:324a       kgc:subject   ResidentPatient:Blessington
12902  ResidentPatient:324a   kgc:hasProperty           word.predicate:hide
12903  ResidentPatient:324a          kgc:what  ResidentPatient:Own_identity

[1394 rows x 3 columns]

This is the model made by Pytorch.

In [14]:
model

KgStoryTransformer03(
  (entity_embeddings): Embedding(7817, 128, padding_idx=0)
  (relation_embeddings): Embedding(67, 64, padding_idx=0)
  (pe): PositionalEncoding(
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (transformer): TransformerEncoder(
    (layers): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiheadAttention(
          (out_proj): NonDynamicallyQuantizableLinear(in_features=128, out_features=128, bias=True)
        )
        (linear1): Linear(in_features=128, out_features=1028, bias=True)
        (dropout): Dropout(p=0.1, inplace=False)
        (linear2): Linear(in_features=1028, out_features=128, bias=True)
        (norm1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (norm2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (dropout1): Dropout(p=0.1, inplace=False)
        (dropout2): Dropout(p=0.1, inplace=False)
        (activation): GELU(approximate='none')
      )
      (1): TransformerEncoderLayer(
      

This function is used to visualize Attention. The description is skipped.

In [15]:
# This is sub functions for getting Attention.
def extract(_model, target, inputs):
    """This is sub functions for getting Attention.

    """
    features = None

    def forward_hook(_module, _inputs, _):
        nonlocal features
        x, _, _ = _inputs
        outputs = _module.forward(x, x, x, need_weights=True)[1]
        features = outputs.detach().clone()

    handle = target.register_forward_hook(forward_hook)

    _model.eval()
    _model(inputs, torch.LongTensor([[]]), torch.LongTensor([[]]), torch.LongTensor([[]]))

    handle.remove()

    return features

# This is main functions for getting Attention.
def get_attention(input_):
    """This is main functions for getting Attention.

    """
    assert len(input_) == 1
    features = extract(model, model.transformer.layers[-1].self_attn, input_)[0]
    df_attention = pd.DataFrame([[entities[h], relations[r], entities[t]]+[features[j, i].item() for j in range(len(features))] for i, (h, r, t) in enumerate(input_[0])])
    df_attention.columns=[HEAD, RELATION, TAIL] + [f'atten_from{i}' for i in range(len(df_attention.columns)-3)]
    return df_attention

def show_attention_heatmap(df_attention):
    sns.heatmap(df_attention.iloc[:,3:])
    plt.show()

In [16]:
MASK_E = DefaultTokens.MASK_E
KILL = 'word.predicate:kill'

TAKE = 'word.predicate:take'
BRING = 'word.predicate:bring'
DIE = 'word.predicate:die'
HIDE = 'word.predicate:hide'

The input to the model is the following function's "question_".
There are some last scenes and criminal scene after last scene.
Each part of criminal scene are changed into a victim or <mask>, and the MASK part is estimated.

In [17]:
bos_triple = [d_e[DefaultTokens.BOS_E], d_r[DefaultTokens.BOS_R],d_e[DefaultTokens.BOS_E]]
mask_e_id = d_e[DefaultTokens.MASK_E]
Holmes_id =d_e['AllTitle:Holmes']

def make_ranking(from_story_name, to_story_name, predicate_, whom_, subject_, why_, what_, where_):
    if not (from_story_name is None and to_story_name is None):
        _start_index = story_entities.index(from_story_name)-1
        _end_index = len(story_entities) - story_entities[::-1].index(to_story_name)
    else:
        _start_index = 0
        _end_index = 0
    question_ = torch.tensor(
        [
            # [... last 80 scenes ...],
            # ...
            bos_triple,
            [mask_e_id, d_r['kgc:infoSource'],     Holmes_id      ],
            [mask_e_id, d_r['kgc:hasPredicate'],   d_e[predicate_]],
            [mask_e_id, d_r['kgc:whom'],           d_e[whom_     ]],
            [mask_e_id, d_r['kgc:subject'],        d_e[subject_  ]],
            [mask_e_id, d_r['kgc:why'],            d_e[why_      ]],
            [mask_e_id, d_r['kgc:what'],           d_e[what_     ]],
            [mask_e_id, d_r['kgc:where'],          d_e[where_    ]],
        ]
    )
    mask_ = torch.zeros_like(question_, dtype=torch.bool) # not mask all position
    mask_[1:, 0] = True                                   # where head position without bos token
    mask_[1:, 2] = True                                   # where tail position without bos token

    last_triples = triple[_start_index: _end_index]

    questions = torch.cat([last_triples, question_], dim=0).unsqueeze(0)
    masks = torch.cat([torch.zeros_like(last_triples), mask_], dim=0).to(torch.bool).transpose(1,0).unsqueeze(0)

    data_list = []
    with torch.no_grad():
        _, (story_pred, relation_pred, entity_pred) = model(questions, masks[:,0], masks[:,1], masks[:,2])
        sorted_ = torch.argsort(entity_pred, dim=1, descending=True)
        for i in range(sorted_.shape[1]):
            ans_= sorted_[:, i]
            info_source_, predicate_pred, whom_pred, subject_pred, why_pred, what_pred, where_pred = ans_
            data_list.append([entities[predicate_pred], entities[whom_pred], entities[subject_pred], entities[why_pred], entities[what_pred], entities[where_pred]])
    df_ranking = pd.DataFrame(data_list, columns=['predicate', 'whom', 'subject', 'why', 'what', 'where'])
    df_attension = get_attention(questions)

    return df_ranking, df_attension

In [18]:
def main_func01(_title, _victim_name, criminal, predicate, _last_index, _story_len):
    from_ = f'{_title}:{_last_index-_story_len+1}'
    to_ = f'{_title}:{_last_index}'
    predicate = predicate
    victim = f'{_title}:{_victim_name}'
    criminal = f'{_title}:{criminal}'
    df_ranking, df_attension = make_ranking(
        from_, to_, predicate, victim, MASK_E, MASK_E, MASK_E, MASK_E)
    df_ranking.index.name='ranking'

    pred_rank = df_ranking.index[df_ranking['subject']==criminal].tolist()
    pred_rank = pred_rank[0] if len(pred_rank)==1 else -1
    logger.info(f"The pred ranking about {criminal} is {pred_rank}")
    display(df_ranking.iloc[:max(20, pred_rank)])
    len_ = len(df_attension)
    for i in range(len_-10, len_):
        print(f"index={i}, triple={df_attension.iloc[i,:3].tolist()}, attention list")
        display(df_attension.sort_values(f'atten_from{i}', ascending=False).iloc[:,[0,1,2,3+i]],)
    return df_ranking, df_attension

def check_killer(_title, _victim_name, _killer_name, _last_index, _story_len):
    return main_func01(_title, _victim_name, _killer_name, KILL, _last_index, _story_len)

# Estimate Criminals

### SpeckledBand(まだらの紐)
Who killed Julia? (criminal & explanation)
被害者: Julia
犯人: Roylott
犯行に用いたもの: snake
犯行動機: 母の相続財産を独占したい

### Input sequence is like this.


|     head     | relation  |            tail            |
|:------------:|:---------:|:--------------------------:|
| SpeckledBand |  stories  |            ...             |
|     ...      |    ...    |            ...             |
|    \<bos>    |  \<bos>   |           \<bos>           |
|  \<unknown>  | predicate |            kill            |
|  \<unknown>  |   whom    |           Julia            |
|  \<unknown>  |  subject  | \<mask(Answer is Roylott)> |
|  \<unknown>  |    why    |          \<mask>           |
|  \<unknown>  |   what    |          \<mask>           |
|  \<unknown>  |    why    |          \<mask>           |

In [19]:
def do_SpeckledBand_pred():
    title = 'SpeckledBand'
    victim_name = 'Julia'
    killer_name = 'Roylott'
    last_index = 401
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention
do_SpeckledBand_pred()
pass

2023-02-04 06:55:14 - INFO - 3696358453.py - 13 - The pred ranking about SpeckledBand:Roylott is 0


predicate                           whom  \
ranking                                                              
0              word.predicate:think           SpeckledBand:Roylott   
1               word.predicate:hear                AllTitle:Holmes   
2              word.predicate:exist             SpeckledBand:snake   
3               word.predicate:want                AllTitle:Watson   
4             word.predicate:return  AbbeyGrange:Lady_Brackenstall   
5                word.predicate:die              DevilsFoot:Brenda   
6            word.predicate:notHave    AbbeyGrange:Stanley_Hopkins   
7                  CrookedMan:Nancy             SpeckledBand:Helen   
8               word.predicate:love               CrookedMan:Nancy   
9               word.predicate:give              DevilsFoot:Porter   
10               word.predicate:say              DancingMen:Cubitt   
11            word.predicate:become   SpeckledBand:Julia_s_bedroom   
12               word.predicate:see           DevilsFoot:Sterndale   
13              word.predicate:find               CrookedMan:Henry   
14             word.predicate:close             SpeckledBand:Julia   
15              word.predicate:send     ACaseOfIdentity:Sutherland   
16       ACaseOfIdentity:Sutherland              CrookedMan:rebels   
17               word.predicate:put        AbbeyGrange:Jack_Croker   
18         AbbeyGrange:cord_of_bell          DancingMen:Abe_Slaney   
19              word.predicate:live         ACaseOfIdentity:Hosmer   

                              subject                            why  \
ranking                                                                
0                SpeckledBand:Roylott   DateTime:1883-04-02T04:00:00   
1                  SpeckledBand:snake   SpeckledBand:VentilationHole   
2                     AllTitle:Holmes              DevilsFoot:Case_1   
3                     AllTitle:Watson           SpeckledBand:Roylott   
4         AbbeyGrange:Stanley_Hopkins               SpeckledBand:bed   
5                DevilsFoot:Sterndale              DevilsFoot:Brenda   
6                   DancingMen:Cubitt               CrookedMan:Nancy   
7                   DevilsFoot:Brenda           DevilsFoot:Sterndale   
8         ResidentPatient:Elderly_man   DateTime:1883-04-01T23:00:00   
9               ACaseOfIdentity:Woman   SpeckledBand:Julia_s_bedroom   
10                word.predicate:find             SpeckledBand:snake   
11         ACaseOfIdentity:Sutherland   SpeckledBand:Helen_s_bedroom   
12       SpeckledBand:Julia_s_bedroom                DevilsFoot:Owen   
13                    DevilsFoot:Owen         ACaseOfIdentity:Hosmer   
14               SpeckledBand:coroner           word.predicate:think   
15                  DevilsFoot:Porter              DancingMen:Cubitt   
16              DancingMen:Sentence_I  SilverBlaze:Inspector_Gregory   
17             SilverBlaze:Ned_Hunter         SilverBlaze:Ned_Hunter   
18                 SpeckledBand:Helen             SpeckledBand:Helen   
19                   SpeckledBand:bed            DancingMen:Letter_Z   

                                  what                           where  
ranking                                                                 
0                   SpeckledBand:snake                SpeckledBand:bed  
1         DateTime:1883-04-02T04:00:00    DateTime:1883-04-02T04:00:00  
2                 DevilsFoot:Sterndale            SpeckledBand:Roylott  
3         SpeckledBand:VentilationHole            DevilsFoot:Sterndale  
4        SilverBlaze:Inspector_Gregory  SpeckledBand:Roylott_s_bedroom  
5                    DancingMen:Cubitt    SpeckledBand:Julia_s_bedroom  
6                    DevilsFoot:Case_1               DevilsFoot:Case_1  
7          ResidentPatient:Elderly_man              SpeckledBand:Helen  
8                   SpeckledBand:chair             DevilsFoot:Roundhay  
9                 SpeckledBand:Roylott   SilverBlaze:Inspector_Gregory  
10            SilverBlaz

index=452, triple=['SpeckledBand:401', 'kgc:subject', 'SpeckledBand:Roma'], attention list


head          relation  \
440  SpeckledBand:399       kgc:subject   
446  SpeckledBand:400       kgc:subject   
313  SpeckledBand:375       kgc:subject   
455          <mask_e>    kgc:infoSource   
396  SpeckledBand:391       kgc:subject   
442  SpeckledBand:399            kgc:to   
461          <mask_e>         kgc:where   
323  SpeckledBand:376          kgc:what   
319  SpeckledBand:375          kgc:time   
434  SpeckledBand:398       kgc:subject   
337  SpeckledBand:378          kgc:when   
412  SpeckledBand:394       kgc:subject   
318  SpeckledBand:375          kgc:when   
296  SpeckledBand:372       kgc:subject   
304  SpeckledBand:373          kgc:when   
302  SpeckledBand:373       kgc:subject   
449  SpeckledBand:400          kgc:when   
310  SpeckledBand:374          kgc:when   
321  SpeckledBand:376       kgc:subject   
325  SpeckledBand:376          kgc:when   
448  SpeckledBand:400          kgc:what   
332  SpeckledBand:377          kgc:when   
436  SpeckledBand:398            kgc:to   
387  SpeckledBand:389  kgc:hasPredicate   
419  SpeckledBand:395          kgc:what   
316  SpeckledBand:375    kgc:infoSource   
457          <mask_e>          kgc:whom   
458          <mask_e>       kgc:subject   
447  SpeckledBand:400  kgc:hasPredicate   
398  SpeckledBand:391          kgc:what   
338  SpeckledBand:378          kgc:time   
452  SpeckledBand:401       kgc:subject   
326  SpeckledBand:376          kgc:time   
399  SpeckledBand:391         kgc:where   
299  SpeckledBand:372          kgc:when   
293  SpeckledBand:371          kgc:when   
352  SpeckledBand:382       kgc:subject   
400  SpeckledBand:391          kgc:when   
335  SpeckledBand:378       kgc:subject   
307  SpeckledBand:374       kgc:subject   
356  SpeckledBand:383       kgc:subject   
407  SpeckledBand:393       kgc:subject   
324  SpeckledBand:376    kgc:infoSource   
391  SpeckledBand:390       kgc:subject   
333  SpeckledBand:377          kgc:time   
311  SpeckledBand:374          kgc:time   
132  SpeckledBand:344          kgc:when   
443  SpeckledBand:399          kgc:when   
305  SpeckledBand:373          kgc:time   
429  SpeckledBand:397       kgc:subject   
459          <mask_e>           kgc:why   
390  SpeckledBand:390       kgc:subject   
315  SpeckledBand:375            kgc:to   
317  SpeckledBand:375          kgc:from   
401  SpeckledBand:391          kgc:time   
403  SpeckledBand:392       kgc:subject   
394  SpeckledBand:390         kgc:where   
322  SpeckledBand:376  kgc:hasPredicate   
331  SpeckledBand:377          kgc:from   
377  SpeckledBand:387       kgc:subject   
388  SpeckledBand:389            kgc:to   
369  SpeckledBand:385       kgc:subject   
230  SpeckledBand:361          kgc:when   
460          <mask_e>          kgc:what   
392  SpeckledBand:390       kgc:subject   
314  SpeckledBand:375  kgc:hasPredicate   
309  SpeckledBand:374            kgc:to   
148  SpeckledBand:347          kgc:when   
373  SpeckledBand:386       kgc:subject   
423  SpeckledBand:396       kgc:subject   
340  SpeckledBand:379       kgc:subject   
414  SpeckledBand:394          kgc:what   
298  SpeckledBand:372            kgc:to   
165  SpeckledBand:350          kgc:when   
276  SpeckledBand:369       kgc:subject   
206  SpeckledBand:357          kgc:when   
294  SpeckledBand:371          kgc:time   
195  SpeckledBand:355          kgc:when   
328  SpeckledBand:377       kgc:subject   
397  SpeckledBand:391  kgc:hasPredicate   
242  SpeckledBand:363          kgc:when   
245  SpeckledBand:364       kgc:subject   
248  SpeckledBand:364    kgc:infoSource   
441  SpeckledBand:399  kgc:hasPredicate   
371  SpeckledBand:385            kgc:to   
270  SpeckledBand:368       kgc:subject   
382  SpeckledBand:388       kgc:subject   
417  SpeckledBand:395       kgc:subject   
249  SpeckledBand:364          kgc:when   
212  SpeckledBand:358          kgc:when   
261  SpeckledBand:366          kgc:when   
405  SpeckledBand:392          kgc:what   
444  SpeckledBand:

index=453, triple=['SpeckledBand:401', 'kgc:hasProperty', 'word.predicate:band'], attention list


...

head          relation  \
337  SpeckledBand:378          kgc:when   
338  SpeckledBand:378          kgc:time   
304  SpeckledBand:373          kgc:when   
319  SpeckledBand:375          kgc:time   
401  SpeckledBand:391          kgc:time   
333  SpeckledBand:377          kgc:time   
326  SpeckledBand:376          kgc:time   
332  SpeckledBand:377          kgc:when   
400  SpeckledBand:391          kgc:when   
293  SpeckledBand:371          kgc:when   
449  SpeckledBand:400          kgc:when   
299  SpeckledBand:372          kgc:when   
305  SpeckledBand:373          kgc:time   
311  SpeckledBand:374          kgc:time   
294  SpeckledBand:371          kgc:time   
310  SpeckledBand:374          kgc:when   
325  SpeckledBand:376          kgc:when   
420  SpeckledBand:395          kgc:when   
318  SpeckledBand:375          kgc:when   
443  SpeckledBand:399          kgc:when   
279  SpeckledBand:369          kgc:when   
280  SpeckledBand:369          kgc:time   
444  SpeckledBand:399          kgc:time   
165  SpeckledBand:350          kgc:when   
258  SpeckledBand:366       kgc:subject   
344  SpeckledBand:379          kgc:time   
343  SpeckledBand:379          kgc:when   
415  SpeckledBand:394          kgc:when   
170  SpeckledBand:351          kgc:when   
421  SpeckledBand:395          kgc:time   
461          <mask_e>         kgc:where   
206  SpeckledBand:357          kgc:when   
450  SpeckledBand:400          kgc:time   
287  SpeckledBand:370          kgc:when   
363  SpeckledBand:383          kgc:time   
248  SpeckledBand:364    kgc:infoSource   
261  SpeckledBand:366          kgc:when   
300  SpeckledBand:372          kgc:time   
132  SpeckledBand:344          kgc:when   
288  SpeckledBand:370          kgc:time   
438  SpeckledBand:398          kgc:time   
142  SpeckledBand:346          kgc:when   
410  SpeckledBand:393          kgc:when   
242  SpeckledBand:363          kgc:when   
255  SpeckledBand:365          kgc:when   
148  SpeckledBand:347          kgc:when   
387  SpeckledBand:389  kgc:hasPredicate   
241  SpeckledBand:363    kgc:infoSource   
259  SpeckledBand:366  kgc:hasPredicate   
137  SpeckledBand:345          kgc:when   
419  SpeckledBand:395          kgc:what   
437  SpeckledBand:398          kgc:when   
446  SpeckledBand:400       kgc:subject   
126  SpeckledBand:343          kgc:when   
397  SpeckledBand:391  kgc:hasPredicate   
440  SpeckledBand:399       kgc:subject   
249  SpeckledBand:364          kgc:when   
273  SpeckledBand:368          kgc:when   
195  SpeckledBand:355          kgc:when   
447  SpeckledBand:400  kgc:hasPredicate   
230  SpeckledBand:361          kgc:when   
254  SpeckledBand:365    kgc:infoSource   
268  SpeckledBand:367          kgc:time   
295           <bos_e>           <bos_r>   
418  SpeckledBand:395  kgc:hasPredicate   
455          <mask_e>    kgc:infoSource   
411           <bos_e>           <bos_r>   
322  SpeckledBand:376  kgc:hasPredicate   
427  SpeckledBand:396          kgc:time   
426  SpeckledBand:396          kgc:when   
416           <bos_e>           <bos_r>   
334           <bos_e>           <bos_r>   
312           <bos_e>           <bos_r>   
301           <bos_e>           <bos_r>   
306           <bos_e>           <bos_r>   
422           <bos_e>           <bos_r>   
402           <bos_e>           <bos_r>   
298  SpeckledBand:372            kgc:to   
412  SpeckledBand:394       kgc:subject   
201  SpeckledBand:356          kgc:when   
406           <bos_e>           <bos_r>   
362  SpeckledBand:383          kgc:when   
289           <bos_e>           <bos_r>   
275           <bos_e>           <bos_r>   
395           <bos_e>           <bos_r>   
345           <bos_e>           <bos_r>   
442  SpeckledBand:399            kgc:to   
445           <bos_e>           <bos_r>   
262  SpeckledBand:366          kgc:time   
274  SpeckledBand:368          kgc:time   
339           <bos_e>           <bos_r>   
459          <mask_e>           kgc:why   
458          <mask

index=460, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
337  SpeckledBand:378          kgc:when   
338  SpeckledBand:378          kgc:time   
304  SpeckledBand:373          kgc:when   
449  SpeckledBand:400          kgc:when   
319  SpeckledBand:375          kgc:time   
293  SpeckledBand:371          kgc:when   
332  SpeckledBand:377          kgc:when   
333  SpeckledBand:377          kgc:time   
325  SpeckledBand:376          kgc:when   
310  SpeckledBand:374          kgc:when   
400  SpeckledBand:391          kgc:when   
318  SpeckledBand:375          kgc:when   
326  SpeckledBand:376          kgc:time   
461          <mask_e>         kgc:where   
299  SpeckledBand:372          kgc:when   
311  SpeckledBand:374          kgc:time   
305  SpeckledBand:373          kgc:time   
401  SpeckledBand:391          kgc:time   
443  SpeckledBand:399          kgc:when   
455          <mask_e>    kgc:infoSource   
440  SpeckledBand:399       kgc:subject   
206  SpeckledBand:357          kgc:when   
446  SpeckledBand:400       kgc:subject   
420  SpeckledBand:395          kgc:when   
442  SpeckledBand:399            kgc:to   
279  SpeckledBand:369          kgc:when   
294  SpeckledBand:371          kgc:time   
436  SpeckledBand:398            kgc:to   
396  SpeckledBand:391       kgc:subject   
242  SpeckledBand:363          kgc:when   
142  SpeckledBand:346          kgc:when   
248  SpeckledBand:364    kgc:infoSource   
343  SpeckledBand:379          kgc:when   
344  SpeckledBand:379          kgc:time   
148  SpeckledBand:347          kgc:when   
415  SpeckledBand:394          kgc:when   
241  SpeckledBand:363    kgc:infoSource   
280  SpeckledBand:369          kgc:time   
302  SpeckledBand:373       kgc:subject   
434  SpeckledBand:398       kgc:subject   
458          <mask_e>       kgc:subject   
165  SpeckledBand:350          kgc:when   
444  SpeckledBand:399          kgc:time   
300  SpeckledBand:372          kgc:time   
298  SpeckledBand:372            kgc:to   
412  SpeckledBand:394       kgc:subject   
261  SpeckledBand:366          kgc:when   
170  SpeckledBand:351          kgc:when   
437  SpeckledBand:398          kgc:when   
132  SpeckledBand:344          kgc:when   
309  SpeckledBand:374            kgc:to   
331  SpeckledBand:377          kgc:from   
296  SpeckledBand:372       kgc:subject   
255  SpeckledBand:365          kgc:when   
457          <mask_e>          kgc:whom   
450  SpeckledBand:400          kgc:time   
410  SpeckledBand:393          kgc:when   
249  SpeckledBand:364          kgc:when   
419  SpeckledBand:395          kgc:what   
363  SpeckledBand:383          kgc:time   
414  SpeckledBand:394          kgc:what   
459          <mask_e>           kgc:why   
411           <bos_e>           <bos_r>   
313  SpeckledBand:375       kgc:subject   
391  SpeckledBand:390       kgc:subject   
388  SpeckledBand:389            kgc:to   
394  SpeckledBand:390         kgc:where   
345           <bos_e>           <bos_r>   
258  SpeckledBand:366       kgc:subject   
287  SpeckledBand:370          kgc:when   
295           <bos_e>           <bos_r>   
334           <bos_e>           <bos_r>   
201  SpeckledBand:356          kgc:when   
438  SpeckledBand:398          kgc:time   
137  SpeckledBand:345          kgc:when   
406           <bos_e>           <bos_r>   
315  SpeckledBand:375            kgc:to   
306           <bos_e>           <bos_r>   
339           <bos_e>           <bos_r>   
126  SpeckledBand:343          kgc:when   
422           <bos_e>           <bos_r>   
416           <bos_e>           <bos_r>   
316  SpeckledBand:375    kgc:infoSource   
402           <bos_e>           <bos_r>   
230  SpeckledBand:361          kgc:when   
385           <bos_e>           <bos_r>   
275           <bos_e>           <bos_r>   
387  SpeckledBand:389  kgc:hasPredicate   
301           <bos_e>           <bos_r>   
312           <bos_e>           <bos_r>   
289           <bos_e>           <bos_r>   
395           <bos_e>           <bos_r>   
281           <bos

index=461, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
337  SpeckledBand:378          kgc:when   
338  SpeckledBand:378          kgc:time   
461          <mask_e>         kgc:where   
304  SpeckledBand:373          kgc:when   
440  SpeckledBand:399       kgc:subject   
434  SpeckledBand:398       kgc:subject   
333  SpeckledBand:377          kgc:time   
446  SpeckledBand:400       kgc:subject   
310  SpeckledBand:374          kgc:when   
319  SpeckledBand:375          kgc:time   
400  SpeckledBand:391          kgc:when   
429  SpeckledBand:397       kgc:subject   
326  SpeckledBand:376          kgc:time   
343  SpeckledBand:379          kgc:when   
401  SpeckledBand:391          kgc:time   
332  SpeckledBand:377          kgc:when   
458          <mask_e>       kgc:subject   
449  SpeckledBand:400          kgc:when   
299  SpeckledBand:372          kgc:when   
443  SpeckledBand:399          kgc:when   
206  SpeckledBand:357          kgc:when   
442  SpeckledBand:399            kgc:to   
455          <mask_e>    kgc:infoSource   
325  SpeckledBand:376          kgc:when   
165  SpeckledBand:350          kgc:when   
293  SpeckledBand:371          kgc:when   
318  SpeckledBand:375          kgc:when   
420  SpeckledBand:395          kgc:when   
344  SpeckledBand:379          kgc:time   
436  SpeckledBand:398            kgc:to   
363  SpeckledBand:383          kgc:time   
305  SpeckledBand:373          kgc:time   
311  SpeckledBand:374          kgc:time   
279  SpeckledBand:369          kgc:when   
142  SpeckledBand:346          kgc:when   
356  SpeckledBand:383       kgc:subject   
394  SpeckledBand:390         kgc:where   
132  SpeckledBand:344          kgc:when   
280  SpeckledBand:369          kgc:time   
307  SpeckledBand:374       kgc:subject   
302  SpeckledBand:373       kgc:subject   
170  SpeckledBand:351          kgc:when   
396  SpeckledBand:391       kgc:subject   
403  SpeckledBand:392       kgc:subject   
126  SpeckledBand:343          kgc:when   
412  SpeckledBand:394       kgc:subject   
287  SpeckledBand:370          kgc:when   
137  SpeckledBand:345          kgc:when   
452  SpeckledBand:401       kgc:subject   
437  SpeckledBand:398          kgc:when   
242  SpeckledBand:363          kgc:when   
419  SpeckledBand:395          kgc:what   
377  SpeckledBand:387       kgc:subject   
294  SpeckledBand:371          kgc:time   
407  SpeckledBand:393       kgc:subject   
335  SpeckledBand:378       kgc:subject   
296  SpeckledBand:372       kgc:subject   
457          <mask_e>          kgc:whom   
248  SpeckledBand:364    kgc:infoSource   
423  SpeckledBand:396       kgc:subject   
148  SpeckledBand:347          kgc:when   
444  SpeckledBand:399          kgc:time   
438  SpeckledBand:398          kgc:time   
431  SpeckledBand:397          kgc:when   
426  SpeckledBand:396          kgc:when   
255  SpeckledBand:365          kgc:when   
340  SpeckledBand:379       kgc:subject   
345           <bos_e>           <bos_r>   
399  SpeckledBand:391         kgc:where   
391  SpeckledBand:390       kgc:subject   
249  SpeckledBand:364          kgc:when   
288  SpeckledBand:370          kgc:time   
392  SpeckledBand:390       kgc:subject   
373  SpeckledBand:386       kgc:subject   
339           <bos_e>           <bos_r>   
306           <bos_e>           <bos_r>   
433           <bos_e>           <bos_r>   
421  SpeckledBand:395          kgc:time   
411           <bos_e>           <bos_r>   
428           <bos_e>           <bos_r>   
334           <bos_e>           <bos_r>   
385           <bos_e>           <bos_r>   
309  SpeckledBand:374            kgc:to   
364           <bos_e>           <bos_r>   
261  SpeckledBand:366          kgc:when   
422           <bos_e>           <bos_r>   
459          <mask_e>           kgc:why   
445           <bos_e>           <bos_r>   
241  SpeckledBand:363    kgc:infoSource   
301           <bos_e>           <bos_r>   
439           <bos_e>           <bos_r>   
273  SpeckledBand:368          kgc:when   
406           <bos

### DevilsFoot(悪魔の足跡１)
Who killed the victims? (criminal & explanation)
被害者: Brenda
犯人: Mortimer
犯行動機: 財産

In [20]:
def do_devil1_pred():
    title = 'DevilsFoot'
    victim_name = 'Brenda'
    killer_name = 'Mortimer'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil1_pred()
pass

2023-02-04 06:55:15 - INFO - 3696358453.py - 13 - The pred ranking about DevilsFoot:Mortimer is 0


predicate                             whom  \
ranking                                                             
0             word.predicate:say              DevilsFoot:Mortimer   
1            word.predicate:meet  ResidentPatient:Percy_Trevelyan   
2            word.predicate:kill                  AllTitle:Holmes   
3           word.predicate:enter                  AllTitle:Watson   
4            word.predicate:find                          <bos_e>   
5              word.predicate:go                DevilsFoot:Brenda   
6           word.predicate:think           ACaseOfIdentity:Hosmer   
7             word.predicate:ask             DevilsFoot:Sterndale   
8           word.predicate:goOut             SpeckledBand:Roylott   
9             word.predicate:see                  DevilsFoot:Owen   
10         word.predicate:become      ResidentPatient:Blessington   
11           word.predicate:love               SpeckledBand:Helen   
12           word.predicate:send                DevilsFoot:George   
13           word.predicate:have         SilverBlaze:John_Straker   
14               AllTitle:Holmes               word.predicate:say   
15           word.predicate:hear                  DevilsFoot:room   
16           word.predicate:call             AbbeyGrange:Criminal   
17       word.predicate:notExist              DevilsFoot:Roundhay   
18           word.predicate:come           word.predicate:examine   
19            word.predicate:die             word.predicate:think   

                                      subject  \
ranking                                         
0                         DevilsFoot:Mortimer   
1                        DevilsFoot:Sterndale   
2                             AllTitle:Holmes   
3             ResidentPatient:Percy_Trevelyan   
4                             AllTitle:Watson   
5                         DevilsFoot:Roundhay   
6                          SpeckledBand:Helen   
7                           DevilsFoot:Brenda   
8                             DevilsFoot:Owen   
9                           DevilsFoot:Porter   
10                            DevilsFoot:room   
11                                    <bos_e>   
12       ACaseOfIdentity:mother_of_Sutherland   
13               DateTime:1883-04-02T04:00:00   
14                          DevilsFoot:George   
15                       SpeckledBand:Roylott   
16                       word.predicate:close   
17                   SilverBlaze:Silver_Blaze   
18                  DevilsFoot:Doctor_Richard   
19                 ACaseOfIdentity:Sutherland   

                                          why  \
ranking                                         
0                           DevilsFoot:Brenda   
1                             DevilsFoot:Owen   
2                         DevilsFoot:Mortimer   
3                             AllTitle:Watson   
4                             DevilsFoot:room   
5                        DevilsFoot:Sterndale   
6                             SilverBlaze:357   
7                            DevilsFoot:table   
8                           DevilsFoot:window   
9                     AbbeyGrange:Jack_Croker   
10                         word.predicate:say   
11                       SilverBlaze:incident   
12            ResidentPatient:Percy_Trevelyan   
13                         SpeckledBand:snake   
14                     DevilsFoot:living_room   
15                        word.predicate:meet   
16       ACaseOfIdentity:mother_of_Sutherland   
17                     ACaseOfIdentity:Hosmer   
18                            SilverBlaze:094   
19           AbbeyGrange:Testimony_of_Theresa   

                                         what  \
ranking                                         
0                         DevilsFoot:Mortimer   
1                        DevilsFoot:Sterndale   
2                           DevilsFoot:Brenda   
3                             DevilsFoot:Owen   
4             ResidentPatient:Percy_Trevelyan   
5  

index=444, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


head          relation  \
445  DevilsFoot:489         kgc:where   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
356  DevilsFoot:473       kgc:subject   
453        <mask_e>         kgc:where   
438  DevilsFoot:488       kgc:subject   
362  DevilsFoot:473          kgc:what   
370  DevilsFoot:473          kgc:what   
359  DevilsFoot:473          kgc:what   
419  DevilsFoot:484       kgc:subject   
414  DevilsFoot:483       kgc:subject   
360  DevilsFoot:473          kgc:what   
368  DevilsFoot:473          kgc:what   
358  DevilsFoot:473          kgc:what   
364  DevilsFoot:473          kgc:what   
451        <mask_e>           kgc:why   
361  DevilsFoot:473          kgc:what   
412  DevilsFoot:482    kgc:infoSource   
444  DevilsFoot:489          kgc:what   
328  DevilsFoot:468       kgc:subject   
329  DevilsFoot:468       kgc:subject   
408  DevilsFoot:482       kgc:subject   
367  DevilsFoot:473          kgc:what   
348  DevilsFoot:471    kgc:infoSource   
365  DevilsFoot:473          kgc:what   
387  DevilsFoot:477    kgc:infoSource   
331  DevilsFoot:468    kgc:infoSource   
341  DevilsFoot:470    kgc:infoSource   
429  DevilsFoot:486       kgc:subject   
372  DevilsFoot:474       kgc:subject   
336  DevilsFoot:469    kgc:infoSource   
424  DevilsFoot:485       kgc:subject   
449        <mask_e>          kgc:whom   
383  DevilsFoot:476    kgc:infoSource   
447        <mask_e>    kgc:infoSource   
376  DevilsFoot:475       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
354  DevilsFoot:472    kgc:infoSource   
427  DevilsFoot:485    kgc:infoSource   
434  DevilsFoot:487       kgc:subject   
442  DevilsFoot:489       kgc:subject   
452        <mask_e>          kgc:what   
378  DevilsFoot:475    kgc:infoSource   
450        <mask_e>       kgc:subject   
306  DevilsFoot:463    kgc:infoSource   
417  DevilsFoot:483    kgc:infoSource   
406  DevilsFoot:481          kgc:from   
436  DevilsFoot:487            kgc:on   
374  DevilsFoot:474    kgc:infoSource   
326  DevilsFoot:467    kgc:infoSource   
371         <bos_e>           <bos_r>   
431  DevilsFoot:486    kgc:infoSource   
380  DevilsFoot:476       kgc:subject   
343  DevilsFoot:471       kgc:subject   
440  DevilsFoot:488         kgc:where   
338  DevilsFoot:470       kgc:subject   
355         <bos_e>           <bos_r>   
375         <bos_e>           <bos_r>   
311  DevilsFoot:464    kgc:infoSource   
316  DevilsFoot:465    kgc:infoSource   
290  DevilsFoot:460    kgc:infoSource   
441         <bos_e>           <bos_r>   
337         <bos_e>           <bos_r>   
327         <bos_e>           <bos_r>   
332         <bos_e>           <bos_r>   
396  DevilsFoot:479    kgc:infoSource   
446         <bos_e>           <bos_r>   
413         <bos_e>           <bos_r>   
323  DevilsFoot:467       kgc:subject   
407         <bos_e>           <bos_r>   
333  DevilsFoot:469       kgc:subject   
391  DevilsFoot:478    kgc:infoSource   
422  DevilsFoot:484    kgc:infoSource   
379         <bos_e>           <bos_r>   
437         <bos_e>           <bos_r>   
402         <bos_e>           <bos_r>   
350  DevilsFoot:472       kgc:subject   
411  DevilsFoot:482            kgc:to   
377  DevilsFoot:475   kgc:hasProperty   
90   DevilsFoot:422    kgc:infoSource   
403  DevilsFoot:481       kgc:subject   
342         <bos_e>           <bos_r>   
418         <bos_e>           <bos_r>   
322         <bos_e>           <bos_r>   
366  DevilsFoot:473          kgc:what   
384         <bos_e>           <bos_r>   
312         <bos_e>           <bos_r>   
349         <bos_e>           <bos_r>   
321  DevilsFoot:466    kgc:infoSource   
307         <bos_e>           <bos_r>   
423         <bos_e>           <bos_r>   
300  DevilsFoot:462    kgc:infoSource   
433         <bos_e>           <bos_r>   
313  DevilsFoot:465       kgc:subject   
230  DevilsFoot:448    kgc:infoSource   
397         <bos_e>           <bos_r>   
401  DevilsFoot:480    kgc:infoSource 

index=445, triple=['DevilsFoot:489', 'kgc:where', 'DevilsFoot:garden_of_Cottage_of_Sterndale'], attention list


...

head          relation  \
356  DevilsFoot:473       kgc:subject   
438  DevilsFoot:488       kgc:subject   
328  DevilsFoot:468       kgc:subject   
414  DevilsFoot:483       kgc:subject   
329  DevilsFoot:468       kgc:subject   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
419  DevilsFoot:484       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
372  DevilsFoot:474       kgc:subject   
408  DevilsFoot:482       kgc:subject   
336  DevilsFoot:469    kgc:infoSource   
331  DevilsFoot:468    kgc:infoSource   
370  DevilsFoot:473          kgc:what   
341  DevilsFoot:470    kgc:infoSource   
429  DevilsFoot:486       kgc:subject   
376  DevilsFoot:475       kgc:subject   
326  DevilsFoot:467    kgc:infoSource   
405  DevilsFoot:481    kgc:infoSource   
362  DevilsFoot:473          kgc:what   
348  DevilsFoot:471    kgc:infoSource   
380  DevilsFoot:476       kgc:subject   
371         <bos_e>           <bos_r>   
338  DevilsFoot:470       kgc:subject   
333  DevilsFoot:469       kgc:subject   
453        <mask_e>         kgc:where   
359  DevilsFoot:473          kgc:what   
364  DevilsFoot:473          kgc:what   
434  DevilsFoot:487       kgc:subject   
378  DevilsFoot:475    kgc:infoSource   
343  DevilsFoot:471       kgc:subject   
383  DevilsFoot:476    kgc:infoSource   
387  DevilsFoot:477    kgc:infoSource   
441         <bos_e>           <bos_r>   
417  DevilsFoot:483    kgc:infoSource   
354  DevilsFoot:472    kgc:infoSource   
375         <bos_e>           <bos_r>   
316  DevilsFoot:465    kgc:infoSource   
327         <bos_e>           <bos_r>   
424  DevilsFoot:485       kgc:subject   
355         <bos_e>           <bos_r>   
450        <mask_e>       kgc:subject   
360  DevilsFoot:473          kgc:what   
311  DevilsFoot:464    kgc:infoSource   
437         <bos_e>           <bos_r>   
306  DevilsFoot:463    kgc:infoSource   
358  DevilsFoot:473          kgc:what   
427  DevilsFoot:485    kgc:infoSource   
446         <bos_e>           <bos_r>   
407         <bos_e>           <bos_r>   
402         <bos_e>           <bos_r>   
445  DevilsFoot:489         kgc:where   
332         <bos_e>           <bos_r>   
374  DevilsFoot:474    kgc:infoSource   
413         <bos_e>           <bos_r>   
337         <bos_e>           <bos_r>   
361  DevilsFoot:473          kgc:what   
418         <bos_e>           <bos_r>   
322         <bos_e>           <bos_r>   
431  DevilsFoot:486    kgc:infoSource   
368  DevilsFoot:473          kgc:what   
379         <bos_e>           <bos_r>   
312         <bos_e>           <bos_r>   
321  DevilsFoot:466    kgc:infoSource   
423         <bos_e>           <bos_r>   
433         <bos_e>           <bos_r>   
307         <bos_e>           <bos_r>   
403  DevilsFoot:481       kgc:subject   
350  DevilsFoot:472       kgc:subject   
290  DevilsFoot:460    kgc:infoSource   
397         <bos_e>           <bos_r>   
449        <mask_e>          kgc:whom   
391  DevilsFoot:478    kgc:infoSource   
393         <bos_e>           <bos_r>   
313  DevilsFoot:465       kgc:subject   
342         <bos_e>           <bos_r>   
317         <bos_e>           <bos_r>   
384         <bos_e>           <bos_r>   
301         <bos_e>           <bos_r>   
349         <bos_e>           <bos_r>   
428         <bos_e>           <bos_r>   
90   DevilsFoot:422    kgc:infoSource   
388         <bos_e>           <bos_r>   
280         <bos_e>           <bos_r>   
451        <mask_e>           kgc:why   
367  DevilsFoot:473          kgc:what   
422  DevilsFoot:484    kgc:infoSource   
300  DevilsFoot:462    kgc:infoSource   
295  DevilsFoot:461    kgc:infoSource   
396  DevilsFoot:479    kgc:infoSource   
365  DevilsFoot:473          kgc:what   
230  DevilsFoot:448    kgc:infoSource   
436  DevilsFoot:487            kgc:on   
236         <bos_e>           <bos_r>   
323  DevilsFoot:467       kgc:subject   
231         <bos_e>           <bos_r>   
274         <bos_e>           <bos_r> 

index=452, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
438  DevilsFoot:488       kgc:subject   
356  DevilsFoot:473       kgc:subject   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
372  DevilsFoot:474       kgc:subject   
329  DevilsFoot:468       kgc:subject   
434  DevilsFoot:487       kgc:subject   
414  DevilsFoot:483       kgc:subject   
450        <mask_e>       kgc:subject   
328  DevilsFoot:468       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
453        <mask_e>         kgc:where   
331  DevilsFoot:468    kgc:infoSource   
370  DevilsFoot:473          kgc:what   
336  DevilsFoot:469    kgc:infoSource   
380  DevilsFoot:476       kgc:subject   
374  DevilsFoot:474    kgc:infoSource   
419  DevilsFoot:484       kgc:subject   
362  DevilsFoot:473          kgc:what   
429  DevilsFoot:486       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
359  DevilsFoot:473          kgc:what   
376  DevilsFoot:475       kgc:subject   
403  DevilsFoot:481       kgc:subject   
408  DevilsFoot:482       kgc:subject   
354  DevilsFoot:472    kgc:infoSource   
378  DevilsFoot:475    kgc:infoSource   
341  DevilsFoot:470    kgc:infoSource   
360  DevilsFoot:473          kgc:what   
364  DevilsFoot:473          kgc:what   
348  DevilsFoot:471    kgc:infoSource   
387  DevilsFoot:477    kgc:infoSource   
358  DevilsFoot:473          kgc:what   
326  DevilsFoot:467    kgc:infoSource   
417  DevilsFoot:483    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
431  DevilsFoot:486    kgc:infoSource   
436  DevilsFoot:487            kgc:on   
338  DevilsFoot:470       kgc:subject   
311  DevilsFoot:464    kgc:infoSource   
343  DevilsFoot:471       kgc:subject   
308  DevilsFoot:464       kgc:subject   
306  DevilsFoot:463    kgc:infoSource   
361  DevilsFoot:473          kgc:what   
368  DevilsFoot:473          kgc:what   
427  DevilsFoot:485    kgc:infoSource   
371         <bos_e>           <bos_r>   
367  DevilsFoot:473          kgc:what   
375         <bos_e>           <bos_r>   
445  DevilsFoot:489         kgc:where   
406  DevilsFoot:481          kgc:from   
327         <bos_e>           <bos_r>   
333  DevilsFoot:469       kgc:subject   
424  DevilsFoot:485       kgc:subject   
391  DevilsFoot:478    kgc:infoSource   
437         <bos_e>           <bos_r>   
355         <bos_e>           <bos_r>   
441         <bos_e>           <bos_r>   
447        <mask_e>    kgc:infoSource   
365  DevilsFoot:473          kgc:what   
332         <bos_e>           <bos_r>   
449        <mask_e>          kgc:whom   
440  DevilsFoot:488         kgc:where   
337         <bos_e>           <bos_r>   
316  DevilsFoot:465    kgc:infoSource   
373  DevilsFoot:474   kgc:hasProperty   
396  DevilsFoot:479    kgc:infoSource   
402         <bos_e>           <bos_r>   
322         <bos_e>           <bos_r>   
407         <bos_e>           <bos_r>   
413         <bos_e>           <bos_r>   
379         <bos_e>           <bos_r>   
389  DevilsFoot:478       kgc:subject   
433         <bos_e>           <bos_r>   
422  DevilsFoot:484    kgc:infoSource   
312         <bos_e>           <bos_r>   
446         <bos_e>           <bos_r>   
321  DevilsFoot:466    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
418         <bos_e>           <bos_r>   
307         <bos_e>           <bos_r>   
350  DevilsFoot:472       kgc:subject   
451        <mask_e>           kgc:why   
342         <bos_e>           <bos_r>   
442  DevilsFoot:489       kgc:subject   
317         <bos_e>           <bos_r>   
423         <bos_e>           <bos_r>   
300  DevilsFoot:462    kgc:infoSource   
384         <bos_e>           <bos_r>   
393         <bos_e>           <bos_r>   
397         <bos_e>           <bos_r>   
302  DevilsFoot:463       kgc:subject   
301         <bos_e>           <bos_r>   
388         <bos_e>           <bos_r>   
435  DevilsFoot:487   kgc:hasProperty   
281  DevilsFoot:459       kgc:subject   
428         <bos_e>           <bos_r> 

index=453, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
438  DevilsFoot:488       kgc:subject   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
434  DevilsFoot:487       kgc:subject   
356  DevilsFoot:473       kgc:subject   
453        <mask_e>         kgc:where   
450        <mask_e>       kgc:subject   
429  DevilsFoot:486       kgc:subject   
329  DevilsFoot:468       kgc:subject   
380  DevilsFoot:476       kgc:subject   
414  DevilsFoot:483       kgc:subject   
364  DevilsFoot:473          kgc:what   
328  DevilsFoot:468       kgc:subject   
362  DevilsFoot:473          kgc:what   
376  DevilsFoot:475       kgc:subject   
403  DevilsFoot:481       kgc:subject   
359  DevilsFoot:473          kgc:what   
405  DevilsFoot:481    kgc:infoSource   
408  DevilsFoot:482       kgc:subject   
370  DevilsFoot:473          kgc:what   
358  DevilsFoot:473          kgc:what   
372  DevilsFoot:474       kgc:subject   
360  DevilsFoot:473          kgc:what   
419  DevilsFoot:484       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
445  DevilsFoot:489         kgc:where   
389  DevilsFoot:478       kgc:subject   
336  DevilsFoot:469    kgc:infoSource   
331  DevilsFoot:468    kgc:infoSource   
343  DevilsFoot:471       kgc:subject   
308  DevilsFoot:464       kgc:subject   
374  DevilsFoot:474    kgc:infoSource   
368  DevilsFoot:473          kgc:what   
387  DevilsFoot:477    kgc:infoSource   
367  DevilsFoot:473          kgc:what   
378  DevilsFoot:475    kgc:infoSource   
333  DevilsFoot:469       kgc:subject   
338  DevilsFoot:470       kgc:subject   
341  DevilsFoot:470    kgc:infoSource   
311  DevilsFoot:464    kgc:infoSource   
354  DevilsFoot:472    kgc:infoSource   
440  DevilsFoot:488         kgc:where   
361  DevilsFoot:473          kgc:what   
365  DevilsFoot:473          kgc:what   
306  DevilsFoot:463    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
348  DevilsFoot:471    kgc:infoSource   
442  DevilsFoot:489       kgc:subject   
431  DevilsFoot:486    kgc:infoSource   
326  DevilsFoot:467    kgc:infoSource   
406  DevilsFoot:481          kgc:from   
391  DevilsFoot:478    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
316  DevilsFoot:465    kgc:infoSource   
302  DevilsFoot:463       kgc:subject   
424  DevilsFoot:485       kgc:subject   
447        <mask_e>    kgc:infoSource   
417  DevilsFoot:483    kgc:infoSource   
350  DevilsFoot:472       kgc:subject   
427  DevilsFoot:485    kgc:infoSource   
275  DevilsFoot:458       kgc:subject   
313  DevilsFoot:465       kgc:subject   
281  DevilsFoot:459       kgc:subject   
449        <mask_e>          kgc:whom   
436  DevilsFoot:487            kgc:on   
396  DevilsFoot:479    kgc:infoSource   
292  DevilsFoot:461       kgc:subject   
353  DevilsFoot:472          kgc:whom   
321  DevilsFoot:466    kgc:infoSource   
451        <mask_e>           kgc:why   
411  DevilsFoot:482            kgc:to   
398  DevilsFoot:480       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
90   DevilsFoot:422    kgc:infoSource   
300  DevilsFoot:462    kgc:infoSource   
295  DevilsFoot:461    kgc:infoSource   
371         <bos_e>           <bos_r>   
357  DevilsFoot:473  kgc:hasPredicate   
401  DevilsFoot:480    kgc:infoSource   
279  DevilsFoot:458    kgc:infoSource   
375         <bos_e>           <bos_r>   
394  DevilsFoot:479       kgc:subject   
290  DevilsFoot:460    kgc:infoSource   
355         <bos_e>           <bos_r>   
437         <bos_e>           <bos_r>   
441         <bos_e>           <bos_r>   
323  DevilsFoot:467       kgc:subject   
452        <mask_e>          kgc:what   
373  DevilsFoot:474   kgc:hasProperty   
273  DevilsFoot:457    kgc:infoSource   
327         <bos_e>           <bos_r>   
183  DevilsFoot:440    kgc:infoSource   
286  DevilsFoot:460       kgc:subject   
366  DevilsFoot:473          kgc:what   
402         <bos_e>           <bos_r>   
435  DevilsFoot:487   kgc:hasProperty   
283  DevilsFoot:459    kgc:infoSource 

### DevilsFoot(悪魔の足跡2)
Who killed the victims? (criminal & explanation)
被害者: Mortimer
犯人: 
犯行動機: 恋人の敵

In [21]:
def do_devil2_pred():
    title = 'DevilsFoot'
    victim_name = 'Mortimer'
    killer_name = 'Sterndale'
    last_index = 489
    story_len = 80
    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_devil2_pred()
pass

2023-02-04 06:55:16 - INFO - 3696358453.py - 13 - The pred ranking about DevilsFoot:Sterndale is 1


predicate                             whom  \
ranking                                                             
0            word.predicate:meet              DevilsFoot:Mortimer   
1             word.predicate:say                  AllTitle:Holmes   
2            word.predicate:kill                  AllTitle:Watson   
3              word.predicate:go  ResidentPatient:Percy_Trevelyan   
4            word.predicate:find                          <bos_e>   
5             word.predicate:see             DevilsFoot:Sterndale   
6           word.predicate:think             SpeckledBand:Roylott   
7           word.predicate:enter                  DevilsFoot:Owen   
8          word.predicate:become               SpeckledBand:Helen   
9           word.predicate:goOut                DevilsFoot:Brenda   
10           word.predicate:hear           ACaseOfIdentity:Hosmer   
11               AllTitle:Holmes                DevilsFoot:George   
12            word.predicate:ask      ResidentPatient:Blessington   
13            word.predicate:die        DevilsFoot:Doctor_Richard   
14           word.predicate:want                DevilsFoot:Porter   
15       word.predicate:notExist                word.predicate:go   
16           word.predicate:love         SilverBlaze:Silver_Blaze   
17           word.predicate:come         SilverBlaze:John_Straker   
18           word.predicate:call              word.predicate:have   
19           word.predicate:send               word.predicate:say   

                                      subject  \
ranking                                         
0                         DevilsFoot:Mortimer   
1                        DevilsFoot:Sterndale   
2                             AllTitle:Holmes   
3                             AllTitle:Watson   
4             ResidentPatient:Percy_Trevelyan   
5                             DevilsFoot:Owen   
6                          SpeckledBand:Helen   
7                           DevilsFoot:Brenda   
8                         DevilsFoot:Roundhay   
9                   DevilsFoot:Doctor_Richard   
10                                    <bos_e>   
11                          DevilsFoot:Porter   
12       ACaseOfIdentity:mother_of_Sutherland   
13                            DevilsFoot:room   
14               DateTime:1883-04-02T04:00:00   
15                          DevilsFoot:George   
16                       word.predicate:close   
17                   SilverBlaze:John_Straker   
18                   SilverBlaze:Silver_Blaze   
19                       SpeckledBand:Roylott   

                                          why  \
ranking                                         
0                           DevilsFoot:Brenda   
1                         DevilsFoot:Mortimer   
2                             DevilsFoot:Owen   
3                             AllTitle:Watson   
4                        DevilsFoot:Sterndale   
5                             DevilsFoot:room   
6                             SilverBlaze:357   
7                     AbbeyGrange:Jack_Croker   
8                           DevilsFoot:window   
9                            DevilsFoot:table   
10                         word.predicate:say   
11                     DevilsFoot:living_room   
12                         SpeckledBand:Helen   
13                     ACaseOfIdentity:Hosmer   
14                       SilverBlaze:incident   
15            ResidentPatient:Percy_Trevelyan   
16       ACaseOfIdentity:mother_of_Sutherland   
17                            SilverBlaze:094   
18                         SilverBlaze:stable   
19                         SpeckledBand:snake   

                                         what                            where  
ranking                                                                         
0                         DevilsFoot:Mortimer              DevilsFoot:Mortimer  
1                        DevilsFoot:Sterndale                DevilsFoot:Brenda  
2                     

index=444, triple=['DevilsFoot:489', 'kgc:what', 'DevilsFoot:gravel'], attention list


head          relation  \
445  DevilsFoot:489         kgc:where   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
453        <mask_e>         kgc:where   
356  DevilsFoot:473       kgc:subject   
438  DevilsFoot:488       kgc:subject   
362  DevilsFoot:473          kgc:what   
370  DevilsFoot:473          kgc:what   
359  DevilsFoot:473          kgc:what   
360  DevilsFoot:473          kgc:what   
419  DevilsFoot:484       kgc:subject   
414  DevilsFoot:483       kgc:subject   
368  DevilsFoot:473          kgc:what   
358  DevilsFoot:473          kgc:what   
364  DevilsFoot:473          kgc:what   
361  DevilsFoot:473          kgc:what   
451        <mask_e>           kgc:why   
412  DevilsFoot:482    kgc:infoSource   
367  DevilsFoot:473          kgc:what   
329  DevilsFoot:468       kgc:subject   
328  DevilsFoot:468       kgc:subject   
408  DevilsFoot:482       kgc:subject   
365  DevilsFoot:473          kgc:what   
348  DevilsFoot:471    kgc:infoSource   
444  DevilsFoot:489          kgc:what   
387  DevilsFoot:477    kgc:infoSource   
341  DevilsFoot:470    kgc:infoSource   
429  DevilsFoot:486       kgc:subject   
331  DevilsFoot:468    kgc:infoSource   
372  DevilsFoot:474       kgc:subject   
450        <mask_e>       kgc:subject   
424  DevilsFoot:485       kgc:subject   
336  DevilsFoot:469    kgc:infoSource   
447        <mask_e>    kgc:infoSource   
383  DevilsFoot:476    kgc:infoSource   
376  DevilsFoot:475       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
434  DevilsFoot:487       kgc:subject   
449        <mask_e>          kgc:whom   
452        <mask_e>          kgc:what   
427  DevilsFoot:485    kgc:infoSource   
354  DevilsFoot:472    kgc:infoSource   
442  DevilsFoot:489       kgc:subject   
417  DevilsFoot:483    kgc:infoSource   
378  DevilsFoot:475    kgc:infoSource   
306  DevilsFoot:463    kgc:infoSource   
374  DevilsFoot:474    kgc:infoSource   
326  DevilsFoot:467    kgc:infoSource   
406  DevilsFoot:481          kgc:from   
380  DevilsFoot:476       kgc:subject   
343  DevilsFoot:471       kgc:subject   
431  DevilsFoot:486    kgc:infoSource   
436  DevilsFoot:487            kgc:on   
371         <bos_e>           <bos_r>   
338  DevilsFoot:470       kgc:subject   
440  DevilsFoot:488         kgc:where   
355         <bos_e>           <bos_r>   
375         <bos_e>           <bos_r>   
316  DevilsFoot:465    kgc:infoSource   
311  DevilsFoot:464    kgc:infoSource   
290  DevilsFoot:460    kgc:infoSource   
337         <bos_e>           <bos_r>   
441         <bos_e>           <bos_r>   
396  DevilsFoot:479    kgc:infoSource   
327         <bos_e>           <bos_r>   
323  DevilsFoot:467       kgc:subject   
332         <bos_e>           <bos_r>   
422  DevilsFoot:484    kgc:infoSource   
391  DevilsFoot:478    kgc:infoSource   
333  DevilsFoot:469       kgc:subject   
413         <bos_e>           <bos_r>   
377  DevilsFoot:475   kgc:hasProperty   
446         <bos_e>           <bos_r>   
350  DevilsFoot:472       kgc:subject   
407         <bos_e>           <bos_r>   
379         <bos_e>           <bos_r>   
411  DevilsFoot:482            kgc:to   
437         <bos_e>           <bos_r>   
402         <bos_e>           <bos_r>   
90   DevilsFoot:422    kgc:infoSource   
403  DevilsFoot:481       kgc:subject   
366  DevilsFoot:473          kgc:what   
342         <bos_e>           <bos_r>   
322         <bos_e>           <bos_r>   
418         <bos_e>           <bos_r>   
384         <bos_e>           <bos_r>   
321  DevilsFoot:466    kgc:infoSource   
312         <bos_e>           <bos_r>   
349         <bos_e>           <bos_r>   
307         <bos_e>           <bos_r>   
300  DevilsFoot:462    kgc:infoSource   
313  DevilsFoot:465       kgc:subject   
423         <bos_e>           <bos_r>   
433         <bos_e>           <bos_r>   
401  DevilsFoot:480    kgc:infoSource   
230  DevilsFoot:448    kgc:infoSource   
325  DevilsFoot:467          kgc:what 

index=445, triple=['DevilsFoot:489', 'kgc:where', 'DevilsFoot:garden_of_Cottage_of_Sterndale'], attention list


...

head          relation  \
356  DevilsFoot:473       kgc:subject   
438  DevilsFoot:488       kgc:subject   
414  DevilsFoot:483       kgc:subject   
328  DevilsFoot:468       kgc:subject   
329  DevilsFoot:468       kgc:subject   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
419  DevilsFoot:484       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
372  DevilsFoot:474       kgc:subject   
408  DevilsFoot:482       kgc:subject   
336  DevilsFoot:469    kgc:infoSource   
331  DevilsFoot:468    kgc:infoSource   
370  DevilsFoot:473          kgc:what   
429  DevilsFoot:486       kgc:subject   
380  DevilsFoot:476       kgc:subject   
341  DevilsFoot:470    kgc:infoSource   
405  DevilsFoot:481    kgc:infoSource   
434  DevilsFoot:487       kgc:subject   
326  DevilsFoot:467    kgc:infoSource   
376  DevilsFoot:475       kgc:subject   
348  DevilsFoot:471    kgc:infoSource   
362  DevilsFoot:473          kgc:what   
453        <mask_e>         kgc:where   
450        <mask_e>       kgc:subject   
364  DevilsFoot:473          kgc:what   
359  DevilsFoot:473          kgc:what   
417  DevilsFoot:483    kgc:infoSource   
387  DevilsFoot:477    kgc:infoSource   
378  DevilsFoot:475    kgc:infoSource   
338  DevilsFoot:470       kgc:subject   
343  DevilsFoot:471       kgc:subject   
333  DevilsFoot:469       kgc:subject   
383  DevilsFoot:476    kgc:infoSource   
371         <bos_e>           <bos_r>   
316  DevilsFoot:465    kgc:infoSource   
354  DevilsFoot:472    kgc:infoSource   
424  DevilsFoot:485       kgc:subject   
306  DevilsFoot:463    kgc:infoSource   
441         <bos_e>           <bos_r>   
360  DevilsFoot:473          kgc:what   
327         <bos_e>           <bos_r>   
375         <bos_e>           <bos_r>   
311  DevilsFoot:464    kgc:infoSource   
358  DevilsFoot:473          kgc:what   
427  DevilsFoot:485    kgc:infoSource   
355         <bos_e>           <bos_r>   
431  DevilsFoot:486    kgc:infoSource   
374  DevilsFoot:474    kgc:infoSource   
361  DevilsFoot:473          kgc:what   
437         <bos_e>           <bos_r>   
368  DevilsFoot:473          kgc:what   
332         <bos_e>           <bos_r>   
337         <bos_e>           <bos_r>   
322         <bos_e>           <bos_r>   
407         <bos_e>           <bos_r>   
446         <bos_e>           <bos_r>   
413         <bos_e>           <bos_r>   
402         <bos_e>           <bos_r>   
418         <bos_e>           <bos_r>   
391  DevilsFoot:478    kgc:infoSource   
290  DevilsFoot:460    kgc:infoSource   
321  DevilsFoot:466    kgc:infoSource   
379         <bos_e>           <bos_r>   
433         <bos_e>           <bos_r>   
312         <bos_e>           <bos_r>   
403  DevilsFoot:481       kgc:subject   
449        <mask_e>          kgc:whom   
423         <bos_e>           <bos_r>   
350  DevilsFoot:472       kgc:subject   
307         <bos_e>           <bos_r>   
445  DevilsFoot:489         kgc:where   
300  DevilsFoot:462    kgc:infoSource   
295  DevilsFoot:461    kgc:infoSource   
313  DevilsFoot:465       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
317         <bos_e>           <bos_r>   
397         <bos_e>           <bos_r>   
342         <bos_e>           <bos_r>   
393         <bos_e>           <bos_r>   
384         <bos_e>           <bos_r>   
301         <bos_e>           <bos_r>   
396  DevilsFoot:479    kgc:infoSource   
367  DevilsFoot:473          kgc:what   
90   DevilsFoot:422    kgc:infoSource   
428         <bos_e>           <bos_r>   
349         <bos_e>           <bos_r>   
452        <mask_e>          kgc:what   
365  DevilsFoot:473          kgc:what   
388         <bos_e>           <bos_r>   
230  DevilsFoot:448    kgc:infoSource   
451        <mask_e>           kgc:why   
302  DevilsFoot:463       kgc:subject   
323  DevilsFoot:467       kgc:subject   
280         <bos_e>           <bos_r>   
308  DevilsFoot:464       kgc:subject   
436  DevilsFoot:487            kgc:on 

index=452, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
438  DevilsFoot:488       kgc:subject   
356  DevilsFoot:473       kgc:subject   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
450        <mask_e>       kgc:subject   
372  DevilsFoot:474       kgc:subject   
329  DevilsFoot:468       kgc:subject   
434  DevilsFoot:487       kgc:subject   
414  DevilsFoot:483       kgc:subject   
453        <mask_e>         kgc:where   
328  DevilsFoot:468       kgc:subject   
412  DevilsFoot:482    kgc:infoSource   
380  DevilsFoot:476       kgc:subject   
331  DevilsFoot:468    kgc:infoSource   
370  DevilsFoot:473          kgc:what   
336  DevilsFoot:469    kgc:infoSource   
419  DevilsFoot:484       kgc:subject   
405  DevilsFoot:481    kgc:infoSource   
374  DevilsFoot:474    kgc:infoSource   
362  DevilsFoot:473          kgc:what   
429  DevilsFoot:486       kgc:subject   
359  DevilsFoot:473          kgc:what   
376  DevilsFoot:475       kgc:subject   
408  DevilsFoot:482       kgc:subject   
403  DevilsFoot:481       kgc:subject   
378  DevilsFoot:475    kgc:infoSource   
341  DevilsFoot:470    kgc:infoSource   
364  DevilsFoot:473          kgc:what   
354  DevilsFoot:472    kgc:infoSource   
348  DevilsFoot:471    kgc:infoSource   
387  DevilsFoot:477    kgc:infoSource   
360  DevilsFoot:473          kgc:what   
417  DevilsFoot:483    kgc:infoSource   
326  DevilsFoot:467    kgc:infoSource   
358  DevilsFoot:473          kgc:what   
383  DevilsFoot:476    kgc:infoSource   
343  DevilsFoot:471       kgc:subject   
306  DevilsFoot:463    kgc:infoSource   
431  DevilsFoot:486    kgc:infoSource   
338  DevilsFoot:470       kgc:subject   
311  DevilsFoot:464    kgc:infoSource   
361  DevilsFoot:473          kgc:what   
308  DevilsFoot:464       kgc:subject   
427  DevilsFoot:485    kgc:infoSource   
436  DevilsFoot:487            kgc:on   
368  DevilsFoot:473          kgc:what   
371         <bos_e>           <bos_r>   
367  DevilsFoot:473          kgc:what   
391  DevilsFoot:478    kgc:infoSource   
375         <bos_e>           <bos_r>   
449        <mask_e>          kgc:whom   
406  DevilsFoot:481          kgc:from   
333  DevilsFoot:469       kgc:subject   
327         <bos_e>           <bos_r>   
424  DevilsFoot:485       kgc:subject   
437         <bos_e>           <bos_r>   
441         <bos_e>           <bos_r>   
365  DevilsFoot:473          kgc:what   
355         <bos_e>           <bos_r>   
445  DevilsFoot:489         kgc:where   
316  DevilsFoot:465    kgc:infoSource   
447        <mask_e>    kgc:infoSource   
332         <bos_e>           <bos_r>   
337         <bos_e>           <bos_r>   
396  DevilsFoot:479    kgc:infoSource   
389  DevilsFoot:478       kgc:subject   
385  DevilsFoot:477       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
440  DevilsFoot:488         kgc:where   
322         <bos_e>           <bos_r>   
373  DevilsFoot:474   kgc:hasProperty   
402         <bos_e>           <bos_r>   
321  DevilsFoot:466    kgc:infoSource   
407         <bos_e>           <bos_r>   
433         <bos_e>           <bos_r>   
413         <bos_e>           <bos_r>   
379         <bos_e>           <bos_r>   
312         <bos_e>           <bos_r>   
418         <bos_e>           <bos_r>   
446         <bos_e>           <bos_r>   
350  DevilsFoot:472       kgc:subject   
302  DevilsFoot:463       kgc:subject   
300  DevilsFoot:462    kgc:infoSource   
307         <bos_e>           <bos_r>   
435  DevilsFoot:487   kgc:hasProperty   
317         <bos_e>           <bos_r>   
342         <bos_e>           <bos_r>   
442  DevilsFoot:489       kgc:subject   
423         <bos_e>           <bos_r>   
384         <bos_e>           <bos_r>   
451        <mask_e>           kgc:why   
393         <bos_e>           <bos_r>   
281  DevilsFoot:459       kgc:subject   
397         <bos_e>           <bos_r>   
301         <bos_e>           <bos_r>   
295  DevilsFoot:461    kgc:infoSource   
388         <bos_e>           <bos_r> 

index=453, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
438  DevilsFoot:488       kgc:subject   
450        <mask_e>       kgc:subject   
434  DevilsFoot:487       kgc:subject   
453        <mask_e>         kgc:where   
363  DevilsFoot:473          kgc:what   
369  DevilsFoot:473          kgc:what   
356  DevilsFoot:473       kgc:subject   
429  DevilsFoot:486       kgc:subject   
380  DevilsFoot:476       kgc:subject   
329  DevilsFoot:468       kgc:subject   
414  DevilsFoot:483       kgc:subject   
364  DevilsFoot:473          kgc:what   
328  DevilsFoot:468       kgc:subject   
376  DevilsFoot:475       kgc:subject   
362  DevilsFoot:473          kgc:what   
405  DevilsFoot:481    kgc:infoSource   
408  DevilsFoot:482       kgc:subject   
359  DevilsFoot:473          kgc:what   
403  DevilsFoot:481       kgc:subject   
389  DevilsFoot:478       kgc:subject   
370  DevilsFoot:473          kgc:what   
419  DevilsFoot:484       kgc:subject   
372  DevilsFoot:474       kgc:subject   
358  DevilsFoot:473          kgc:what   
412  DevilsFoot:482    kgc:infoSource   
360  DevilsFoot:473          kgc:what   
343  DevilsFoot:471       kgc:subject   
445  DevilsFoot:489         kgc:where   
331  DevilsFoot:468    kgc:infoSource   
336  DevilsFoot:469    kgc:infoSource   
308  DevilsFoot:464       kgc:subject   
374  DevilsFoot:474    kgc:infoSource   
378  DevilsFoot:475    kgc:infoSource   
368  DevilsFoot:473          kgc:what   
387  DevilsFoot:477    kgc:infoSource   
367  DevilsFoot:473          kgc:what   
333  DevilsFoot:469       kgc:subject   
338  DevilsFoot:470       kgc:subject   
442  DevilsFoot:489       kgc:subject   
341  DevilsFoot:470    kgc:infoSource   
311  DevilsFoot:464    kgc:infoSource   
385  DevilsFoot:477       kgc:subject   
306  DevilsFoot:463    kgc:infoSource   
361  DevilsFoot:473          kgc:what   
354  DevilsFoot:472    kgc:infoSource   
348  DevilsFoot:471    kgc:infoSource   
365  DevilsFoot:473          kgc:what   
440  DevilsFoot:488         kgc:where   
431  DevilsFoot:486    kgc:infoSource   
326  DevilsFoot:467    kgc:infoSource   
391  DevilsFoot:478    kgc:infoSource   
302  DevilsFoot:463       kgc:subject   
406  DevilsFoot:481          kgc:from   
424  DevilsFoot:485       kgc:subject   
383  DevilsFoot:476    kgc:infoSource   
316  DevilsFoot:465    kgc:infoSource   
417  DevilsFoot:483    kgc:infoSource   
447        <mask_e>    kgc:infoSource   
449        <mask_e>          kgc:whom   
427  DevilsFoot:485    kgc:infoSource   
275  DevilsFoot:458       kgc:subject   
350  DevilsFoot:472       kgc:subject   
313  DevilsFoot:465       kgc:subject   
281  DevilsFoot:459       kgc:subject   
436  DevilsFoot:487            kgc:on   
396  DevilsFoot:479    kgc:infoSource   
292  DevilsFoot:461       kgc:subject   
398  DevilsFoot:480       kgc:subject   
422  DevilsFoot:484    kgc:infoSource   
321  DevilsFoot:466    kgc:infoSource   
411  DevilsFoot:482            kgc:to   
451        <mask_e>           kgc:why   
300  DevilsFoot:462    kgc:infoSource   
452        <mask_e>          kgc:what   
295  DevilsFoot:461    kgc:infoSource   
279  DevilsFoot:458    kgc:infoSource   
401  DevilsFoot:480    kgc:infoSource   
353  DevilsFoot:472          kgc:whom   
394  DevilsFoot:479       kgc:subject   
435  DevilsFoot:487   kgc:hasProperty   
90   DevilsFoot:422    kgc:infoSource   
371         <bos_e>           <bos_r>   
273  DevilsFoot:457    kgc:infoSource   
323  DevilsFoot:467       kgc:subject   
375         <bos_e>           <bos_r>   
357  DevilsFoot:473  kgc:hasPredicate   
373  DevilsFoot:474   kgc:hasProperty   
290  DevilsFoot:460    kgc:infoSource   
355         <bos_e>           <bos_r>   
437         <bos_e>           <bos_r>   
432  DevilsFoot:486          kgc:when   
441         <bos_e>           <bos_r>   
286  DevilsFoot:460       kgc:subject   
327         <bos_e>           <bos_r>   
283  DevilsFoot:459    kgc:infoSource   
325  DevilsFoot:467          kgc:what   
366  DevilsFoot:473          kgc:what 

### AbbeyGrange(僧坊荘園)
Who killed Lord Blackenstall? (criminal & explanation)
被害者: Sir_Eustace_Brackenstall
犯人: 
犯行動機:

In [22]:
def do_AbbeyGrange_pred():
    title = 'AbbeyGrange'
    victim_name = 'Sir_Eustace_Brackenstall'
    killer_name = 'Jack_Croker'
    last_index = 414
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_AbbeyGrange_pred()
pass

2023-02-04 06:55:17 - INFO - 3696358453.py - 13 - The pred ranking about AbbeyGrange:Jack_Croker is 1


predicate                             whom  \
ranking                                                            
0           word.predicate:kill                  AllTitle:Holmes   
1           word.predicate:meet                          <bos_e>   
2             word.predicate:go    AbbeyGrange:Lady_Brackenstall   
3            CrookedMan:Barclay       ACaseOfIdentity:Sutherland   
4          word.predicate:enter                  AllTitle:Watson   
5            word.predicate:see  ResidentPatient:Percy_Trevelyan   
6         word.predicate:inform          AbbeyGrange:Jack_Croker   
7            word.predicate:say      AbbeyGrange:Stanley_Hopkins   
8           word.predicate:come                word.predicate:go   
9               AllTitle:Holmes              AbbeyGrange:Theresa   
10          word.predicate:find      ResidentPatient:Blessington   
11         word.predicate:visit             SpeckledBand:Roylott   
12         word.predicate:goOut           ACaseOfIdentity:Hosmer   
13          word.predicate:know    AbbeyGrange:Thought_of_Holmes   
14         word.predicate:think           CrookedMan:living_room   
15          word.predicate:want                DevilsFoot:Porter   
16           word.predicate:try                  DancingMen:Maid   
17        word.predicate:become              DevilsFoot:Mortimer   
18         word.predicate:exist           word.predicate:examine   
19       word.predicate:notWant              word.predicate:find   

                                 subject  \
ranking                                    
0                        AllTitle:Holmes   
1                AbbeyGrange:Jack_Croker   
2          AbbeyGrange:Lady_Brackenstall   
3             ACaseOfIdentity:Sutherland   
4            AbbeyGrange:Stanley_Hopkins   
5                        AllTitle:Watson   
6           SpeckledBand:Julia_s_bedroom   
7                      word.predicate:go   
8                    AbbeyGrange:Theresa   
9                     AbbeyGrange:police   
10            ResidentPatient:Helper_boy   
11                word.predicate:examine   
12                     CrookedMan:police   
13       ResidentPatient:Percy_Trevelyan   
14                      DancingMen:Elsie   
15                     DevilsFoot:Porter   
16                               <bos_e>   
17                CrookedMan:living_room   
18                   word.predicate:find   
19         AbbeyGrange:Thought_of_Holmes   

                                          why  \
ranking                                         
0                     AbbeyGrange:Jack_Croker   
1                SpeckledBand:Julia_s_bedroom   
2                           CrookedMan:police   
3                DateTime:1883-04-01T15:00:00   
4                             AllTitle:Holmes   
5                          word.predicate:see   
6                 ResidentPatient:Elderly_man   
7                         word.predicate:come   
8                           word.predicate:go   
9                  ACaseOfIdentity:Sutherland   
10                           CrookedMan:beast   
11       AbbeyGrange:Sir_Eustace_Brackenstall   
12               DateTime:1883-04-02T04:00:00   
13                         SpeckledBand:money   
14                          DevilsFoot:Case_1   
15                  ResidentPatient:Footprint   
16                       SpeckledBand:coroner   
17                      word.predicate:inform   
18                     word.predicate:notWant   
19                AbbeyGrange:Stanley_Hopkins   

                                          what  \
ranking                                          
0                              AllTitle:Holmes   
1                   ACaseOfIdentity:Sutherland   
2                    ACaseOfIdentity:Windibank   
3                 SpeckledBand:Julia_s_bedroom   
4                              AllTitle:Watson   
5                            word.predicate:go   
6                              DevilsFoot:lamp   
7                      Abbe

index=416, triple=['AbbeyGrange:414', 'kgc:hasPredicate', 'word.predicate:cannotFind'], attention list


head          relation  \
357   AbbeyGrange:402       kgc:subject   
407   AbbeyGrange:412       kgc:subject   
410   AbbeyGrange:413       kgc:subject   
422          <mask_e>       kgc:subject   
397   AbbeyGrange:410       kgc:subject   
252   AbbeyGrange:382         kgc:where   
402   AbbeyGrange:411       kgc:subject   
323   AbbeyGrange:396       kgc:subject   
293   AbbeyGrange:391       kgc:subject   
419          <mask_e>    kgc:infoSource   
400   AbbeyGrange:410    kgc:infoSource   
415   AbbeyGrange:414       kgc:subject   
253   AbbeyGrange:382    kgc:infoSource   
319   AbbeyGrange:395       kgc:subject   
425          <mask_e>         kgc:where   
289   AbbeyGrange:390  kgc:hasPredicate   
405   AbbeyGrange:411    kgc:infoSource   
412   AbbeyGrange:413          kgc:what   
423          <mask_e>           kgc:why   
250   AbbeyGrange:382       kgc:subject   
385   AbbeyGrange:407            kgc:to   
337   AbbeyGrange:399       kgc:subject   
421          <mask_e>          kgc:whom   
327   AbbeyGrange:397       kgc:subject   
342  AbbeyGrange:399a       kgc:subject   
291   AbbeyGrange:390           kgc:why   
301   AbbeyGrange:392          kgc:what   
332   AbbeyGrange:398       kgc:subject   
290   AbbeyGrange:390    kgc:infoSource   
340   AbbeyGrange:399    kgc:infoSource   
234   AbbeyGrange:379       kgc:subject   
372   AbbeyGrange:405       kgc:subject   
408   AbbeyGrange:412   kgc:hasProperty   
330   AbbeyGrange:397    kgc:infoSource   
297   AbbeyGrange:391          kgc:when   
299   AbbeyGrange:392       kgc:subject   
296   AbbeyGrange:391    kgc:infoSource   
247   AbbeyGrange:381          kgc:what   
358   AbbeyGrange:402   kgc:hasProperty   
229   AbbeyGrange:378       kgc:subject   
413   AbbeyGrange:413    kgc:infoSource   
345  AbbeyGrange:399a    kgc:infoSource   
335   AbbeyGrange:398    kgc:infoSource   
256   AbbeyGrange:383  kgc:hasPredicate   
255   AbbeyGrange:383       kgc:subject   
393   AbbeyGrange:409       kgc:subject   
367   AbbeyGrange:404       kgc:subject   
324   AbbeyGrange:396   kgc:hasProperty   
248   AbbeyGrange:381    kgc:infoSource   
300   AbbeyGrange:392  kgc:hasPredicate   
237   AbbeyGrange:379         kgc:where   
257   AbbeyGrange:383          kgc:what   
374   AbbeyGrange:405    kgc:infoSource   
325   AbbeyGrange:396    kgc:infoSource   
311   AbbeyGrange:393          kgc:when   
334   AbbeyGrange:398          kgc:what   
242   AbbeyGrange:380          kgc:what   
238   AbbeyGrange:379    kgc:infoSource   
240   AbbeyGrange:380       kgc:subject   
321   AbbeyGrange:395    kgc:infoSource   
339   AbbeyGrange:399          kgc:what   
365   AbbeyGrange:403    kgc:infoSource   
236   AbbeyGrange:379          kgc:what   
307   AbbeyGrange:393       kgc:subject   
361   AbbeyGrange:403       kgc:subject   
245   AbbeyGrange:381       kgc:subject   
284   AbbeyGrange:389       kgc:subject   
352   AbbeyGrange:401       kgc:subject   
303  AbbeyGrange:392a       kgc:subject   
398   AbbeyGrange:410  kgc:hasPredicate   
232   AbbeyGrange:378    kgc:infoSource   
359   AbbeyGrange:402    kgc:infoSource   
395   AbbeyGrange:409    kgc:infoSource   
288   AbbeyGrange:390       kgc:subject   
364   AbbeyGrange:403          kgc:whom   
305  AbbeyGrange:392a          kgc:what   
246   AbbeyGrange:381  kgc:hasPredicate   
386   AbbeyGrange:407    kgc:infoSource   
417   AbbeyGrange:414          kgc:what   
314   AbbeyGrange:394       kgc:subject   
243   AbbeyGrange:380    kgc:infoSource   
320   AbbeyGrange:395   kgc:hasProperty   
282   AbbeyGrange:388    kgc:infoSource   
355   AbbeyGrange:401    kgc:infoSource   
201   AbbeyGrange:372    kgc:infoSource   
260   AbbeyGrange:384  kgc:hasPredicate   
379   AbbeyGrange:406          kgc:what   
329   AbbeyGrange:397          kgc:what   
369   AbbeyGrange:404          kgc:whom   
310   AbbeyGrange:393    kgc:infoSource   
196   AbbeyGrange:371    kgc:infoSource   
150   AbbeyGrange:363    kgc:infoSource   
266   AbbeyGrange:

index=417, triple=['AbbeyGrange:414', 'kgc:what', 'AbbeyGrange:False_charge_person'], attention list


...

head          relation  \
422          <mask_e>       kgc:subject   
357   AbbeyGrange:402       kgc:subject   
385   AbbeyGrange:407            kgc:to   
334   AbbeyGrange:398          kgc:what   
257   AbbeyGrange:383          kgc:what   
397   AbbeyGrange:410       kgc:subject   
421          <mask_e>          kgc:whom   
252   AbbeyGrange:382         kgc:where   
399   AbbeyGrange:410          kgc:what   
410   AbbeyGrange:413       kgc:subject   
329   AbbeyGrange:397          kgc:what   
301   AbbeyGrange:392          kgc:what   
253   AbbeyGrange:382    kgc:infoSource   
250   AbbeyGrange:382       kgc:subject   
379   AbbeyGrange:406          kgc:what   
398   AbbeyGrange:410  kgc:hasPredicate   
407   AbbeyGrange:412       kgc:subject   
419          <mask_e>    kgc:infoSource   
293   AbbeyGrange:391       kgc:subject   
400   AbbeyGrange:410    kgc:infoSource   
337   AbbeyGrange:399       kgc:subject   
423          <mask_e>           kgc:why   
412   AbbeyGrange:413          kgc:what   
281   AbbeyGrange:388          kgc:what   
297   AbbeyGrange:391          kgc:when   
330   AbbeyGrange:397    kgc:infoSource   
247   AbbeyGrange:381          kgc:what   
386   AbbeyGrange:407    kgc:infoSource   
236   AbbeyGrange:379          kgc:what   
372   AbbeyGrange:405       kgc:subject   
342  AbbeyGrange:399a       kgc:subject   
271   AbbeyGrange:386          kgc:what   
248   AbbeyGrange:381    kgc:infoSource   
245   AbbeyGrange:381       kgc:subject   
237   AbbeyGrange:379         kgc:where   
327   AbbeyGrange:397       kgc:subject   
345  AbbeyGrange:399a    kgc:infoSource   
255   AbbeyGrange:383       kgc:subject   
191   AbbeyGrange:370    kgc:infoSource   
198   AbbeyGrange:372       kgc:subject   
282   AbbeyGrange:388    kgc:infoSource   
339   AbbeyGrange:399          kgc:what   
384   AbbeyGrange:407          kgc:what   
332   AbbeyGrange:398       kgc:subject   
261   AbbeyGrange:384          kgc:what   
365   AbbeyGrange:403    kgc:infoSource   
417   AbbeyGrange:414          kgc:what   
347   AbbeyGrange:400       kgc:subject   
242   AbbeyGrange:380          kgc:what   
393   AbbeyGrange:409       kgc:subject   
335   AbbeyGrange:398    kgc:infoSource   
377   AbbeyGrange:406       kgc:subject   
290   AbbeyGrange:390    kgc:infoSource   
425          <mask_e>         kgc:where   
402   AbbeyGrange:411       kgc:subject   
201   AbbeyGrange:372    kgc:infoSource   
323   AbbeyGrange:396       kgc:subject   
350   AbbeyGrange:400    kgc:infoSource   
243   AbbeyGrange:380    kgc:infoSource   
340   AbbeyGrange:399    kgc:infoSource   
156   AbbeyGrange:364    kgc:infoSource   
291   AbbeyGrange:390           kgc:why   
352   AbbeyGrange:401       kgc:subject   
358   AbbeyGrange:402   kgc:hasProperty   
160   AbbeyGrange:365    kgc:infoSource   
296   AbbeyGrange:391    kgc:infoSource   
420          <mask_e>  kgc:hasPredicate   
193   AbbeyGrange:371       kgc:subject   
415   AbbeyGrange:414       kgc:subject   
299   AbbeyGrange:392       kgc:subject   
305  AbbeyGrange:392a          kgc:what   
380   AbbeyGrange:406    kgc:infoSource   
240   AbbeyGrange:380       kgc:subject   
382   AbbeyGrange:407       kgc:subject   
203   AbbeyGrange:373       kgc:subject   
153   AbbeyGrange:364       kgc:subject   
196   AbbeyGrange:371    kgc:infoSource   
361   AbbeyGrange:403       kgc:subject   
284   AbbeyGrange:389       kgc:subject   
288   AbbeyGrange:390       kgc:subject   
359   AbbeyGrange:402    kgc:infoSource   
395   AbbeyGrange:409    kgc:infoSource   
390   AbbeyGrange:408          kgc:what   
238   AbbeyGrange:379    kgc:infoSource   
229   AbbeyGrange:378       kgc:subject   
391   AbbeyGrange:408            kgc:to   
355   AbbeyGrange:401    kgc:infoSource   
10    AbbeyGrange:336          kgc:when   
269   AbbeyGrange:386       kgc:subject   
265   AbbeyGrange:385          kgc:what   
206   AbbeyGrange:373    kgc:infoSource   
328   AbbeyGrange:397  kgc:hasPredicate   
325   AbbeyGrange:

index=424, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
422          <mask_e>       kgc:subject   
357   AbbeyGrange:402       kgc:subject   
257   AbbeyGrange:383          kgc:what   
421          <mask_e>          kgc:whom   
410   AbbeyGrange:413       kgc:subject   
301   AbbeyGrange:392          kgc:what   
419          <mask_e>    kgc:infoSource   
385   AbbeyGrange:407            kgc:to   
293   AbbeyGrange:391       kgc:subject   
412   AbbeyGrange:413          kgc:what   
253   AbbeyGrange:382    kgc:infoSource   
407   AbbeyGrange:412       kgc:subject   
252   AbbeyGrange:382         kgc:where   
334   AbbeyGrange:398          kgc:what   
415   AbbeyGrange:414       kgc:subject   
397   AbbeyGrange:410       kgc:subject   
242   AbbeyGrange:380          kgc:what   
345  AbbeyGrange:399a    kgc:infoSource   
281   AbbeyGrange:388          kgc:what   
423          <mask_e>           kgc:why   
329   AbbeyGrange:397          kgc:what   
379   AbbeyGrange:406          kgc:what   
250   AbbeyGrange:382       kgc:subject   
339   AbbeyGrange:399          kgc:what   
247   AbbeyGrange:381          kgc:what   
340   AbbeyGrange:399    kgc:infoSource   
271   AbbeyGrange:386          kgc:what   
282   AbbeyGrange:388    kgc:infoSource   
337   AbbeyGrange:399       kgc:subject   
323   AbbeyGrange:396       kgc:subject   
425          <mask_e>         kgc:where   
236   AbbeyGrange:379          kgc:what   
372   AbbeyGrange:405       kgc:subject   
400   AbbeyGrange:410    kgc:infoSource   
290   AbbeyGrange:390    kgc:infoSource   
344  AbbeyGrange:399a          kgc:what   
367   AbbeyGrange:404       kgc:subject   
342  AbbeyGrange:399a       kgc:subject   
330   AbbeyGrange:397    kgc:infoSource   
299   AbbeyGrange:392       kgc:subject   
276   AbbeyGrange:387            kgc:to   
417   AbbeyGrange:414          kgc:what   
305  AbbeyGrange:392a          kgc:what   
386   AbbeyGrange:407    kgc:infoSource   
335   AbbeyGrange:398    kgc:infoSource   
248   AbbeyGrange:381    kgc:infoSource   
365   AbbeyGrange:403    kgc:infoSource   
319   AbbeyGrange:395       kgc:subject   
265   AbbeyGrange:385          kgc:what   
307   AbbeyGrange:393       kgc:subject   
384   AbbeyGrange:407          kgc:what   
296   AbbeyGrange:391    kgc:infoSource   
424          <mask_e>          kgc:what   
261   AbbeyGrange:384          kgc:what   
393   AbbeyGrange:409       kgc:subject   
350   AbbeyGrange:400    kgc:infoSource   
327   AbbeyGrange:397       kgc:subject   
352   AbbeyGrange:401       kgc:subject   
361   AbbeyGrange:403       kgc:subject   
359   AbbeyGrange:402    kgc:infoSource   
332   AbbeyGrange:398       kgc:subject   
404   AbbeyGrange:411          kgc:what   
355   AbbeyGrange:401    kgc:infoSource   
368   AbbeyGrange:404  kgc:hasPredicate   
402   AbbeyGrange:411       kgc:subject   
347   AbbeyGrange:400       kgc:subject   
297   AbbeyGrange:391          kgc:when   
380   AbbeyGrange:406    kgc:infoSource   
377   AbbeyGrange:406       kgc:subject   
291   AbbeyGrange:390           kgc:why   
267   AbbeyGrange:385           kgc:why   
374   AbbeyGrange:405    kgc:infoSource   
390   AbbeyGrange:408          kgc:what   
255   AbbeyGrange:383       kgc:subject   
237   AbbeyGrange:379         kgc:where   
399   AbbeyGrange:410          kgc:what   
243   AbbeyGrange:380    kgc:infoSource   
277   AbbeyGrange:387          kgc:from   
286   AbbeyGrange:389          kgc:what   
354   AbbeyGrange:401          kgc:what   
201   AbbeyGrange:372    kgc:infoSource   
238   AbbeyGrange:379    kgc:infoSource   
266   AbbeyGrange:385    kgc:infoSource   
413   AbbeyGrange:413    kgc:infoSource   
232   AbbeyGrange:378    kgc:infoSource   
391   AbbeyGrange:408            kgc:to   
245   AbbeyGrange:381       kgc:subject   
358   AbbeyGrange:402   kgc:hasProperty   
303  AbbeyGrange:392a       kgc:subject   
395   AbbeyGrange:409    kgc:infoSource   
314   AbbeyGrange:394       kgc:subject   
240   AbbeyGrange:380       kgc:subject   
198   AbbeyGrange:

index=425, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
357   AbbeyGrange:402       kgc:subject   
422          <mask_e>       kgc:subject   
407   AbbeyGrange:412       kgc:subject   
397   AbbeyGrange:410       kgc:subject   
410   AbbeyGrange:413       kgc:subject   
415   AbbeyGrange:414       kgc:subject   
323   AbbeyGrange:396       kgc:subject   
385   AbbeyGrange:407            kgc:to   
421          <mask_e>          kgc:whom   
393   AbbeyGrange:409       kgc:subject   
252   AbbeyGrange:382         kgc:where   
293   AbbeyGrange:391       kgc:subject   
337   AbbeyGrange:399       kgc:subject   
257   AbbeyGrange:383          kgc:what   
372   AbbeyGrange:405       kgc:subject   
319   AbbeyGrange:395       kgc:subject   
419          <mask_e>    kgc:infoSource   
301   AbbeyGrange:392          kgc:what   
412   AbbeyGrange:413          kgc:what   
425          <mask_e>         kgc:where   
334   AbbeyGrange:398          kgc:what   
367   AbbeyGrange:404       kgc:subject   
250   AbbeyGrange:382       kgc:subject   
423          <mask_e>           kgc:why   
379   AbbeyGrange:406          kgc:what   
327   AbbeyGrange:397       kgc:subject   
358   AbbeyGrange:402   kgc:hasProperty   
236   AbbeyGrange:379          kgc:what   
237   AbbeyGrange:379         kgc:where   
361   AbbeyGrange:403       kgc:subject   
253   AbbeyGrange:382    kgc:infoSource   
400   AbbeyGrange:410    kgc:infoSource   
307   AbbeyGrange:393       kgc:subject   
242   AbbeyGrange:380          kgc:what   
402   AbbeyGrange:411       kgc:subject   
342  AbbeyGrange:399a       kgc:subject   
347   AbbeyGrange:400       kgc:subject   
391   AbbeyGrange:408            kgc:to   
382   AbbeyGrange:407       kgc:subject   
330   AbbeyGrange:397    kgc:infoSource   
339   AbbeyGrange:399          kgc:what   
395   AbbeyGrange:409    kgc:infoSource   
281   AbbeyGrange:388          kgc:what   
424          <mask_e>          kgc:what   
332   AbbeyGrange:398       kgc:subject   
350   AbbeyGrange:400    kgc:infoSource   
247   AbbeyGrange:381          kgc:what   
386   AbbeyGrange:407    kgc:infoSource   
417   AbbeyGrange:414          kgc:what   
259   AbbeyGrange:384       kgc:subject   
377   AbbeyGrange:406       kgc:subject   
329   AbbeyGrange:397          kgc:what   
404   AbbeyGrange:411          kgc:what   
314   AbbeyGrange:394       kgc:subject   
352   AbbeyGrange:401       kgc:subject   
324   AbbeyGrange:396   kgc:hasProperty   
299   AbbeyGrange:392       kgc:subject   
384   AbbeyGrange:407          kgc:what   
399   AbbeyGrange:410          kgc:what   
279   AbbeyGrange:388       kgc:subject   
255   AbbeyGrange:383       kgc:subject   
345  AbbeyGrange:399a    kgc:infoSource   
408   AbbeyGrange:412   kgc:hasProperty   
388   AbbeyGrange:408       kgc:subject   
355   AbbeyGrange:401    kgc:infoSource   
359   AbbeyGrange:402    kgc:infoSource   
405   AbbeyGrange:411    kgc:infoSource   
291   AbbeyGrange:390           kgc:why   
325   AbbeyGrange:396    kgc:infoSource   
413   AbbeyGrange:413    kgc:infoSource   
320   AbbeyGrange:395   kgc:hasProperty   
271   AbbeyGrange:386          kgc:what   
340   AbbeyGrange:399    kgc:infoSource   
303  AbbeyGrange:392a       kgc:subject   
276   AbbeyGrange:387            kgc:to   
288   AbbeyGrange:390       kgc:subject   
305  AbbeyGrange:392a          kgc:what   
365   AbbeyGrange:403    kgc:infoSource   
321   AbbeyGrange:395    kgc:infoSource   
390   AbbeyGrange:408          kgc:what   
380   AbbeyGrange:406    kgc:infoSource   
344  AbbeyGrange:399a          kgc:what   
374   AbbeyGrange:405    kgc:infoSource   
364   AbbeyGrange:403          kgc:whom   
240   AbbeyGrange:380       kgc:subject   
354   AbbeyGrange:401          kgc:what   
297   AbbeyGrange:391          kgc:when   
335   AbbeyGrange:398    kgc:infoSource   
308   AbbeyGrange:393   kgc:hasProperty   
245   AbbeyGrange:381       kgc:subject   
198   AbbeyGrange:372       kgc:subject   
248   AbbeyGrange:381    kgc:infoSource   
296   AbbeyGrange:

### 入院患者
Who killed Blessington? (criminal & explanation)
被害者: Blessington
犯人: 3人
犯行動機:

In [23]:
def do_ResidentPatient_pred():
    title = 'ResidentPatient'
    victim_name = 'Blessington'
    killer_name = ''
    last_index = 324
    story_len = 80

    df_ranking, df_attention = check_killer(title, victim_name, killer_name, last_index, story_len)
    return df_ranking, df_attention

do_ResidentPatient_pred()

2023-02-04 06:55:18 - INFO - 3696358453.py - 13 - The pred ranking about ResidentPatient: is -1


predicate                              whom  \
ranking                                                              
0           word.predicate:enter       ResidentPatient:Blessington   
1            word.predicate:meet          SilverBlaze:Silver_Blaze   
2            word.predicate:kill         ResidentPatient:Young_man   
3              word.predicate:go                   AllTitle:Holmes   
4            word.predicate:find                           <bos_e>   
5            word.predicate:want   ResidentPatient:Percy_Trevelyan   
6         word.predicate:notHave  SilverBlaze:Wife_of_John_Straker   
7            word.predicate:have               word.predicate:have   
8            word.predicate:come       ResidentPatient:Elderly_man   
9             word.predicate:say                   AllTitle:Watson   
10           word.predicate:hear       AbbeyGrange:Stanley_Hopkins   
11               AllTitle:Holmes                 word.predicate:go   
12            word.predicate:see              AbbeyGrange:Criminal   
13           word.predicate:live            ACaseOfIdentity:Hosmer   
14            word.predicate:die   SpeckledBand:mansion_of_Roylott   
15           word.predicate:know                  CrookedMan:Nancy   
16       word.predicate:notExist                 DancingMen:Cubitt   
17          word.predicate:marry           SilverBlaze:Silas_Brown   
18          word.predicate:exist                 DevilsFoot:Porter   
19          word.predicate:goOut     AbbeyGrange:Lady_Brackenstall   

                                  subject  \
ranking                                     
0             ResidentPatient:Blessington   
1               ResidentPatient:Young_man   
2                SilverBlaze:Silver_Blaze   
3                         AllTitle:Holmes   
4             ResidentPatient:Elderly_man   
5         ResidentPatient:Percy_Trevelyan   
6              ResidentPatient:Helper_boy   
7                       word.predicate:go   
8                         AllTitle:Watson   
9             AbbeyGrange:Stanley_Hopkins   
10       SilverBlaze:Wife_of_John_Straker   
11                      DancingMen:Cubitt   
12                SilverBlaze:Silas_Brown   
13                    word.predicate:have   
14       ResidentPatient:Lanner_Inspector   
15          AbbeyGrange:Thought_of_Holmes   
16                AbbeyGrange:dining_room   
17                       CrookedMan:Nancy   
18                     SpeckledBand:Julia   
19                    word.predicate:live   

                                         why  \
ranking                                        
0               DateTime:1883-04-02T02:00:00   
1           ResidentPatient:Blessington_room   
2                         word.predicate:see   
3                 SpeckledBand:1883-04-01T16   
4                    AbbeyGrange:Jack_Croker   
5         ResidentPatient:two_butts_of_Cigar   
6        ResidentPatient:1889-10-21T07:00:00   
7                   SilverBlaze:Edith_Baxter   
8         SilverBlaze:Corpse_of_John_Straker   
9                ResidentPatient:Elderly_man   
10                         AbbeyGrange:truth   
11              SpeckledBand:Julia_s_bedroom   
12              SpeckledBand:Helen_s_bedroom   
13                        SpeckledBand:money   
14                 ACaseOfIdentity:Windibank   
15                        SilverBlaze:stable   
16                         DevilsFoot:Case_1   
17          ResidentPatient:Examination_room   
18                      word.predicate:marry   
19              DateTime:1883-04-01T15:00:00   

                                     what  \
ranking                                     
0                SilverBlaze:Silver_Blaze   
1             ResidentPatient:Blessington   
2           SilverBlaze:Inspector_Gregory   
3               ResidentPatient:Young_man   
4                SilverBlaze:Edith_Baxter   
5                DancingMen:Dancing_dolls   
6                       DevilsFoot:Case_1   
7             ResidentPatient

index=411, triple=['ResidentPatient:324', 'kgc:hasProperty', 'word.predicate:want'], attention list


head          relation  \
400   ResidentPatient:321          kgc:when   
420              <mask_e>         kgc:where   
248   ResidentPatient:293       kgc:subject   
418              <mask_e>           kgc:why   
412   ResidentPatient:324          kgc:what   
304   ResidentPatient:302          kgc:time   
408   ResidentPatient:323          kgc:what   
395   ResidentPatient:320       kgc:subject   
419              <mask_e>          kgc:what   
398   ResidentPatient:321       kgc:subject   
335   ResidentPatient:308          kgc:when   
404   ResidentPatient:322          kgc:what   
332   ResidentPatient:308       kgc:subject   
410   ResidentPatient:324       kgc:subject   
285   ResidentPatient:299          kgc:when   
302   ResidentPatient:302          kgc:what   
361   ResidentPatient:314       kgc:subject   
237   ResidentPatient:291       kgc:subject   
275   ResidentPatient:297            kgc:to   
247   ResidentPatient:293       kgc:subject   
250   ResidentPatient:293          kgc:what   
286   ResidentPatient:299          kgc:when   
393  ResidentPatient:319a          kgc:what   
227   ResidentPatient:288            kgc:on   
337   ResidentPatient:309       kgc:subject   
231   ResidentPatient:289          kgc:what   
414              <mask_e>    kgc:infoSource   
298   ResidentPatient:301          kgc:time   
310   ResidentPatient:303          kgc:time   
370   ResidentPatient:316          kgc:what   
347   ResidentPatient:310          kgc:when   
364   ResidentPatient:315       kgc:subject   
327   ResidentPatient:306          kgc:what   
350   ResidentPatient:311       kgc:subject   
341  ResidentPatient:309a       kgc:subject   
296   ResidentPatient:301          kgc:what   
387   ResidentPatient:319          kgc:what   
338   ResidentPatient:309  kgc:hasPredicate   
396   ResidentPatient:320  kgc:hasPredicate   
287   ResidentPatient:299          kgc:time   
323  ResidentPatient:305a          kgc:what   
339   ResidentPatient:309          kgc:what   
246   ResidentPatient:293       kgc:subject   
351   ResidentPatient:311       kgc:subject   
329   ResidentPatient:307       kgc:subject   
235   ResidentPatient:290          kgc:what   
127   ResidentPatient:271          kgc:what   
417              <mask_e>       kgc:subject   
280   ResidentPatient:298          kgc:what   
406   ResidentPatient:323       kgc:subject   
238   ResidentPatient:291  kgc:hasPredicate   
368   ResidentPatient:316       kgc:subject   
348   ResidentPatient:310          kgc:time   
392  ResidentPatient:319a  kgc:hasPredicate   
356   ResidentPatient:312          kgc:what   
415              <mask_e>  kgc:hasPredicate   
346   ResidentPatient:310          kgc:when   
303   ResidentPatient:302          kgc:when   
301   ResidentPatient:302  kgc:hasPredicate   
202   ResidentPatient:283    kgc:infoSource   
411   ResidentPatient:324   kgc:hasProperty   
402   ResidentPatient:322       kgc:subject   
333   ResidentPatient:308  kgc:hasPredicate   
399   ResidentPatient:321   kgc:hasProperty   
2     ResidentPatient:245       kgc:subject   
366   ResidentPatient:315          kgc:what   
376   ResidentPatient:317          kgc:what   
309   ResidentPatient:303          kgc:when   
358   ResidentPatient:313       kgc:subject   
200   ResidentPatient:283       kgc:subject   
321  ResidentPatient:305a       kgc:subject   
279   ResidentPatient:298          kgc:what   
334   ResidentPatient:308          kgc:whom   
297   ResidentPatient:301          kgc:when   
416              <mask_e>          kgc:whom   
325   ResidentPatient:306       kgc:subject   
369   ResidentPatient:316  kgc:hasPredicate   
308   ResidentPatient:303          kgc:what   
256  ResidentPatient:293a          kgc:what   
55    ResidentPatient:257            kgc:to   
385   ResidentPatient:319       kgc:subject   
223   ResidentPatient:287          kgc:what   
254  ResidentPatient:293a       kgc:subject   
198   ResidentPatient:282    kgc:infoSource   
306   ResidentPatient:303 

index=412, triple=['ResidentPatient:324', 'kgc:what', 'ResidentPatient:324a'], attention list


...

index=419, triple=['<mask_e>', 'kgc:what', '<mask_e>'], attention list


head          relation  \
400   ResidentPatient:321          kgc:when   
408   ResidentPatient:323          kgc:what   
327   ResidentPatient:306          kgc:what   
418              <mask_e>           kgc:why   
332   ResidentPatient:308       kgc:subject   
285   ResidentPatient:299          kgc:when   
419              <mask_e>          kgc:what   
286   ResidentPatient:299          kgc:when   
414              <mask_e>    kgc:infoSource   
227   ResidentPatient:288            kgc:on   
337   ResidentPatient:309       kgc:subject   
350   ResidentPatient:311       kgc:subject   
304   ResidentPatient:302          kgc:time   
417              <mask_e>       kgc:subject   
335   ResidentPatient:308          kgc:when   
416              <mask_e>          kgc:whom   
298   ResidentPatient:301          kgc:time   
334   ResidentPatient:308          kgc:whom   
351   ResidentPatient:311       kgc:subject   
415              <mask_e>  kgc:hasPredicate   
412   ResidentPatient:324          kgc:what   
287   ResidentPatient:299          kgc:time   
420              <mask_e>         kgc:where   
347   ResidentPatient:310          kgc:when   
341  ResidentPatient:309a       kgc:subject   
406   ResidentPatient:323       kgc:subject   
202   ResidentPatient:283    kgc:infoSource   
325   ResidentPatient:306       kgc:subject   
302   ResidentPatient:302          kgc:what   
348   ResidentPatient:310          kgc:time   
346   ResidentPatient:310          kgc:when   
404   ResidentPatient:322          kgc:what   
354   ResidentPatient:312       kgc:subject   
339   ResidentPatient:309          kgc:what   
333   ResidentPatient:308  kgc:hasPredicate   
284   ResidentPatient:299  kgc:hasPredicate   
237   ResidentPatient:291       kgc:subject   
289   ResidentPatient:300       kgc:subject   
221   ResidentPatient:287       kgc:subject   
275   ResidentPatient:297            kgc:to   
368   ResidentPatient:316       kgc:subject   
217   ResidentPatient:286         kgc:where   
402   ResidentPatient:322       kgc:subject   
240   ResidentPatient:292       kgc:subject   
361   ResidentPatient:314       kgc:subject   
344   ResidentPatient:310       kgc:subject   
296   ResidentPatient:301          kgc:what   
233   ResidentPatient:290       kgc:subject   
329   ResidentPatient:307       kgc:subject   
46    ResidentPatient:255          kgc:time   
398   ResidentPatient:321       kgc:subject   
330   ResidentPatient:307   kgc:hasProperty   
231   ResidentPatient:289          kgc:what   
374   ResidentPatient:317       kgc:subject   
370   ResidentPatient:316          kgc:what   
273   ResidentPatient:297       kgc:subject   
220   ResidentPatient:287       kgc:subject   
364   ResidentPatient:315       kgc:subject   
393  ResidentPatient:319a          kgc:what   
208   ResidentPatient:285       kgc:subject   
395   ResidentPatient:320       kgc:subject   
318   ResidentPatient:305       kgc:subject   
410   ResidentPatient:324       kgc:subject   
280   ResidentPatient:298          kgc:what   
372   ResidentPatient:317       kgc:subject   
207   ResidentPatient:285       kgc:subject   
310   ResidentPatient:303          kgc:time   
407   ResidentPatient:323   kgc:hasProperty   
373   ResidentPatient:317       kgc:subject   
294   ResidentPatient:301       kgc:subject   
322  ResidentPatient:305a  kgc:hasPredicate   
198   ResidentPatient:282    kgc:infoSource   
326   ResidentPatient:306  kgc:hasPredicate   
209   ResidentPatient:285       kgc:subject   
274   ResidentPatient:297  kgc:hasPredicate   
281   ResidentPatient:298          kgc:what   
276               <bos_e>           <bos_r>   
241   ResidentPatient:292       kgc:subject   
272   ResidentPatient:297       kgc:subject   
263               <bos_e>           <bos_r>   
248   ResidentPatient:293       kgc:subject   
267               <bos_e>           <bos_r>   
162   ResidentPatient:275         kgc:where   
358   ResidentPatient:313       kgc:subject   
311               <bos_e> 

index=420, triple=['<mask_e>', 'kgc:where', '<mask_e>'], attention list


head          relation  \
400   ResidentPatient:321          kgc:when   
332   ResidentPatient:308       kgc:subject   
285   ResidentPatient:299          kgc:when   
408   ResidentPatient:323          kgc:what   
286   ResidentPatient:299          kgc:when   
304   ResidentPatient:302          kgc:time   
327   ResidentPatient:306          kgc:what   
337   ResidentPatient:309       kgc:subject   
298   ResidentPatient:301          kgc:time   
418              <mask_e>           kgc:why   
350   ResidentPatient:311       kgc:subject   
351   ResidentPatient:311       kgc:subject   
419              <mask_e>          kgc:what   
341  ResidentPatient:309a       kgc:subject   
302   ResidentPatient:302          kgc:what   
420              <mask_e>         kgc:where   
318   ResidentPatient:305       kgc:subject   
335   ResidentPatient:308          kgc:when   
325   ResidentPatient:306       kgc:subject   
415              <mask_e>  kgc:hasPredicate   
287   ResidentPatient:299          kgc:time   
354   ResidentPatient:312       kgc:subject   
334   ResidentPatient:308          kgc:whom   
217   ResidentPatient:286         kgc:where   
347   ResidentPatient:310          kgc:when   
329   ResidentPatient:307       kgc:subject   
414              <mask_e>    kgc:infoSource   
237   ResidentPatient:291       kgc:subject   
275   ResidentPatient:297            kgc:to   
346   ResidentPatient:310          kgc:when   
289   ResidentPatient:300       kgc:subject   
406   ResidentPatient:323       kgc:subject   
417              <mask_e>       kgc:subject   
412   ResidentPatient:324          kgc:what   
296   ResidentPatient:301          kgc:what   
330   ResidentPatient:307   kgc:hasProperty   
361   ResidentPatient:314       kgc:subject   
227   ResidentPatient:288            kgc:on   
348   ResidentPatient:310          kgc:time   
333   ResidentPatient:308  kgc:hasPredicate   
221   ResidentPatient:287       kgc:subject   
273   ResidentPatient:297       kgc:subject   
398   ResidentPatient:321       kgc:subject   
402   ResidentPatient:322       kgc:subject   
202   ResidentPatient:283    kgc:infoSource   
240   ResidentPatient:292       kgc:subject   
207   ResidentPatient:285       kgc:subject   
364   ResidentPatient:315       kgc:subject   
283   ResidentPatient:299       kgc:subject   
339   ResidentPatient:309          kgc:what   
272   ResidentPatient:297       kgc:subject   
321  ResidentPatient:305a       kgc:subject   
278   ResidentPatient:298  kgc:hasPredicate   
241   ResidentPatient:292       kgc:subject   
344   ResidentPatient:310       kgc:subject   
284   ResidentPatient:299  kgc:hasPredicate   
277   ResidentPatient:298       kgc:subject   
395   ResidentPatient:320       kgc:subject   
294   ResidentPatient:301       kgc:subject   
220   ResidentPatient:287       kgc:subject   
247   ResidentPatient:293       kgc:subject   
358   ResidentPatient:313       kgc:subject   
306   ResidentPatient:303       kgc:subject   
74    ResidentPatient:262  kgc:hasPredicate   
303   ResidentPatient:302          kgc:when   
297   ResidentPatient:301          kgc:when   
310   ResidentPatient:303          kgc:time   
301   ResidentPatient:302  kgc:hasPredicate   
410   ResidentPatient:324       kgc:subject   
374   ResidentPatient:317       kgc:subject   
246   ResidentPatient:293       kgc:subject   
315   ResidentPatient:304       kgc:subject   
416              <mask_e>          kgc:whom   
404   ResidentPatient:322          kgc:what   
248   ResidentPatient:293       kgc:subject   
368   ResidentPatient:316       kgc:subject   
407   ResidentPatient:323   kgc:hasProperty   
300   ResidentPatient:302       kgc:subject   
219   ResidentPatient:287       kgc:subject   
392  ResidentPatient:319a  kgc:hasPredicate   
162   ResidentPatient:275         kgc:where   
290   ResidentPatient:300       kgc:subject   
373   ResidentPatient:317       kgc:subject   
208   ResidentPatient:285       kgc:subject   
225   ResidentPatient:288 

(                          predicate                         whom  \
 ranking                                                            
 0              word.predicate:enter  ResidentPatient:Blessington   
 1               word.predicate:meet     SilverBlaze:Silver_Blaze   
 2               word.predicate:kill    ResidentPatient:Young_man   
 3                 word.predicate:go              AllTitle:Holmes   
 4               word.predicate:find                      <bos_e>   
 ...                             ...                          ...   
 7812                 DevilsFoot:263              DevilsFoot:Room   
 7813               SpeckledBand:321               CrookedMan:063   
 7814                 CrookedMan:063          word.predicate:Have   
 7815     AbbeyGrange:French_windows      ACaseOfIdentity:Quickly   
 7816                AbbeyGrange:390              AbbeyGrange:232   
 
                              subject                               why  \
 ranking                  

### 白銀
Who took out the White Silver Blaze? (criminal & explanation) 
被害者: Silver_Blaze
犯人: 
犯行動機:

In [24]:
victim = 'SilverBlaze:Silver_Blaze'
df_ranking_SilverBlaze, df_attension_SilverBlaze = make_ranking(
    'SilverBlaze:330', 'SilverBlaze:396', BRING, MASK_E, MASK_E, MASK_E, victim, MASK_E)

display(df_ranking_SilverBlaze.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_SilverBlaze)
for i in range(len_-20, len_):
    display(i, df_attension_SilverBlaze.iloc[i,:3].tolist())
    display(df_attension_SilverBlaze.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                             whom  \
0        word.predicate:enter         SilverBlaze:Silver_Blaze   
1           word.predicate:go                  AllTitle:Holmes   
2    SilverBlaze:Silver_Blaze      ResidentPatient:Blessington   
3         word.predicate:live         SilverBlaze:John_Straker   
4         word.predicate:have        ResidentPatient:Young_man   
5             AllTitle:Holmes               SilverBlaze:police   
6          word.predicate:say       SpeckledBand:1883-04-01T15   
7         word.predicate:kill          SilverBlaze:Silas_Brown   
8      word.predicate:notHave  ResidentPatient:Percy_Trevelyan   
9        word.predicate:marry                word.predicate:go   
10         word.predicate:die    SilverBlaze:Inspector_Gregory   
11        word.predicate:meet     SpeckledBand:VentilationHole   
12    SilverBlaze:Silas_Brown             SpeckledBand:Roylott   
13  ACaseOfIdentity:Windibank                 CrookedMan:Henry   
14         word.predicate:get      AbbeyGrange:Stanley_Hopkins   
15        word.predicate:want         SilverBlaze:Edith_Baxter   
16  ResidentPatient:Young_man                          <bos_e>   
17       word.predicate:visit         SilverBlaze:Colonel_Ross   
18    word.predicate:notExist            DancingMen:Abe_Slaney   
19      word.predicate:become               SpeckledBand:snake   

                            subject                               why  \
0          SilverBlaze:Silver_Blaze        SpeckledBand:1883-04-01T15   
1                   AllTitle:Holmes               SilverBlaze:Profits   
2          SilverBlaze:John_Straker                   SilverBlaze:394   
3       ResidentPatient:Blessington                   SilverBlaze:275   
4           SilverBlaze:Silas_Brown        SpeckledBand:1883-04-02T04   
5         ResidentPatient:Young_man                   SilverBlaze:385   
6                SilverBlaze:police      DateTime:1883-04-02T02:00:00   
7              SpeckledBand:Roylott       SilverBlaze:Fitzroy_Simpson   
8        SpeckledBand:1883-04-01T15           AbbeyGrange:Jack_Croker   
9                   AllTitle:Watson  SilverBlaze:Wife_of_John_Straker   
10     SpeckledBand:VentilationHole                 DancingMen:Cubitt   
11       SpeckledBand:1883-04-02T04    SilverBlaze:John_Straker_house   
12                 CrookedMan:Henry                   DevilsFoot:Owen   
13      AbbeyGrange:Stanley_Hopkins            ACaseOfIdentity:letter   
14      SilverBlaze:Fitzroy_Simpson          SilverBlaze:John_Straker   
15      ResidentPatient:Elderly_man      DateTime:1883-04-01T12:00:00   
16  ResidentPatient:Percy_Trevelyan            SilverBlaze:Ned_Hunter   
17                word.predicate:go                word.predicate:sit   
18               SpeckledBand:snake       DancingMen:1898-08-13T03:00   
19                DancingMen:Cubitt         SilverBlaze:Along_the_way   

                               what                          where  
0          SilverBlaze:Silver_Blaze       SilverBlaze:Silver_Blaze  
1         ResidentPatient:Young_man                        <bos_e>  
2       ResidentPatient:Blessington       DancingMen:Dancing_dolls  
3                   AllTitle:Holmes              SilverBlaze:Horse  
4                           <bos_e>     SpeckledBand:1883-04-01T15  
5             DancingMen:Abe_Slaney      ResidentPatient:Young_man  
6   ResidentPatient:Percy_Trevelyan       SilverBlaze:Edith_Baxter  
7          SilverBlaze:Edith_Baxter          DancingMen:Abe_Slaney  
8                   AllTitle:Watson           word.predicate:white  
9     SilverBlaze:Inspector_Gregory   DateTime:1883-04-01T12:00:00  
10       SpeckledBand:1883-04-01T15  SilverBlaze:Inspector_Gregory  
11                SilverBlaze:Horse    ResidentPatient:Blessington  
12      AbbeyGrange:Stanley_Hopkins        ResidentPatient:invader  
13              word.predicate:live         word.predicate:confirm  
14               SpeckledBand:snake         SilverBlaze:Desborou

364

['SilverBlaze:394', 'kgc:hasPredicate', 'word.predicate:buy']

head          relation  \
284   SilverBlaze:379  kgc:hasPredicate   
383          <mask_e>         kgc:where   
317   SilverBlaze:386  kgc:hasPredicate   
356   SilverBlaze:393  kgc:hasPredicate   
377          <mask_e>    kgc:infoSource   
331   SilverBlaze:388  kgc:hasPredicate   
364   SilverBlaze:394  kgc:hasPredicate   
327  SilverBlaze:387a  kgc:hasPredicate   
381          <mask_e>           kgc:why   
340   SilverBlaze:390  kgc:hasPredicate   
369   SilverBlaze:395          kgc:what   
363   SilverBlaze:394       kgc:subject   
360  SilverBlaze:393a  kgc:hasPredicate   
368   SilverBlaze:395  kgc:hasPredicate   
337   SilverBlaze:389          kgc:what   
344  SilverBlaze:390a          kgc:what   
283   SilverBlaze:379       kgc:subject   
365   SilverBlaze:394          kgc:what   
328  SilverBlaze:387a          kgc:what   
357   SilverBlaze:393          kgc:what   

                                         tail  atten_from364  
284                  word.predicate:cultivate       0.010447  
383                                  <mask_e>       0.010177  
317                       word.predicate:fire       0.009161  
356                         word.predicate:go       0.008770  
377                           AllTitle:Holmes       0.008569  
331                      word.predicate:smash       0.008228  
364                        word.predicate:buy       0.007722  
327                       word.predicate:feel       0.007655  
381                                  <mask_e>       0.007001  
340                       word.predicate:fall       0.006922  
369                          SilverBlaze:debt       0.006881  
363                  SilverBlaze:John_Straker       0.006640  
360                    word.predicate:confirm       0.006544  
368                       word.predicate:have       0.006226  
337  SilverBlaze:The_forehead_of_John_Straker       0.006033  
344         SilverBlaze:thigh_of_John_Straker       0.005986  
283                  SilverBlaze:John_Straker       0.005956  
365             SilverBlaze:Expensive_clothes       0.005871  
328                        SilverBlaze:Danger       0.005822  
357       SilverBlaze:the_hat_decoration_shop       0.005784

----------


...

----------


383

['<mask_e>', 'kgc:where', '<mask_e>']

head          relation                              tail  \
383          <mask_e>         kgc:where                          <mask_e>   
186  SilverBlaze:359a       kgc:subject                 SilverBlaze:Night   
189  SilverBlaze:359b       kgc:subject                  SilverBlaze:Menu   
283   SilverBlaze:379       kgc:subject          SilverBlaze:John_Straker   
201   SilverBlaze:361       kgc:subject  SilverBlaze:Wife_of_John_Straker   
363   SilverBlaze:394       kgc:subject          SilverBlaze:John_Straker   
342  SilverBlaze:390a       kgc:subject          SilverBlaze:John_Straker   
356   SilverBlaze:393  kgc:hasPredicate                 word.predicate:go   
346   SilverBlaze:391       kgc:subject          SilverBlaze:John_Straker   
351   SilverBlaze:392       kgc:subject          SilverBlaze:John_Straker   
200   SilverBlaze:361       kgc:subject          SilverBlaze:John_Straker   
330   SilverBlaze:388       kgc:subject          SilverBlaze:John_Straker   
380          <mask_e>       kgc:subject                          <mask_e>   
372   SilverBlaze:396       kgc:subject          SilverBlaze:Colonel_Ross   
307   SilverBlaze:384       kgc:subject          SilverBlaze:John_Straker   
213   SilverBlaze:364       kgc:subject              SilverBlaze:Criminal   
379          <mask_e>          kgc:whom                          <mask_e>   
267   SilverBlaze:376       kgc:subject          SilverBlaze:John_Straker   
312   SilverBlaze:385       kgc:subject          SilverBlaze:John_Straker   
316   SilverBlaze:386       kgc:subject          SilverBlaze:John_Straker   

     atten_from383  
383       0.012983  
186       0.011156  
189       0.010974  
283       0.010969  
201       0.010904  
363       0.010808  
342       0.010153  
356       0.009884  
346       0.009824  
351       0.009453  
200       0.009337  
330       0.009000  
380       0.008774  
372       0.008605  
307       0.007911  
213       0.007713  
379       0.007303  
267       0.007110  
312       0.007075  
316       0.006842

----------


### CrookedMan(背中の曲がった男):
Why did Barclay die?
被害者: Barclay
犯人:
犯行動機:

In [25]:
victim = 'CrookedMan:Barclay'
df_ranking_CrookedMan, df_attension_CrookedMan = make_ranking(
    f'CrookedMan:{373-80+1}', 'CrookedMan:373', DIE, MASK_E, victim, MASK_E, MASK_E, MASK_E)

display(df_ranking_CrookedMan.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_CrookedMan)
for i in range(len_-20, len_):
    display(i, df_attension_CrookedMan.iloc[i,:3].tolist())
    display(df_attension_CrookedMan.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")

predicate                           whom  \
0         word.predicate:live             CrookedMan:Barclay   
1          word.predicate:die               CrookedMan:Nancy   
2        word.predicate:enter                AllTitle:Holmes   
3        word.predicate:exist              CrookedMan:police   
4             AllTitle:Holmes               DancingMen:Elsie   
5         word.predicate:want             word.predicate:see   
6   ACaseOfIdentity:Windibank              CrookedMan:Murphy   
7       word.predicate:escape            word.predicate:wear   
8     word.predicate:notExist             SpeckledBand:Julia   
9          word.predicate:see           word.predicate:exist   
10         word.predicate:try               CrookedMan:beast   
11          word.predicate:go            CrookedMan:coachman   
12        word.predicate:meet          word.predicate:return   
13       word.predicate:think              word.predicate:go   
14        word.predicate:give            word.predicate:find   
15      word.predicate:return           word.predicate:think   
16          DevilsFoot:Case_1              DancingMen:Cubitt   
17          CrookedMan:Murphy            CrookedMan:Morrison   
18      word.predicate:notSay  AbbeyGrange:Lady_Brackenstall   
19        word.predicate:find               CrookedMan:Henry   

                          subject                            why  \
0              CrookedMan:Barclay            DancingMen:Letter_Z   
1               DancingMen:Cubitt       SilverBlaze:Edith_Baxter   
2                 AllTitle:Holmes              DancingMen:Cubitt   
3               CrookedMan:police  SilverBlaze:Inspector_Gregory   
4          SilverBlaze:Ned_Hunter              DevilsFoot:Case_1   
5               word.predicate:go               DancingMen:Elsie   
6              SpeckledBand:Julia      ACaseOfIdentity:Windibank   
7                CrookedMan:Nancy           SpeckledBand:Roylott   
8         SilverBlaze:Silas_Brown              AbbeyGrange:truth   
9   AbbeyGrange:Lady_Brackenstall   DateTime:1881-12-01T10:00:00   
10           SpeckledBand:Roylott          DancingMen:Sentence_I   
11               DancingMen:Elsie               CrookedMan:Henry   
12      ResidentPatient:Young_man             CrookedMan:Barclay   
13            CrookedMan:coachman   DateTime:1898-08-10T00:00:00   
14    AbbeyGrange:Stanley_Hopkins            DancingMen:telegram   
15               CrookedMan:Henry                DevilsFoot:Owen   
16    ResidentPatient:Elderly_man        SilverBlaze:Silas_Brown   
17            word.predicate:want             word.predicate:see   
18  AbbeyGrange:Thought_of_Holmes     SpeckledBand:1881-04-01T10   
19             word.predicate:see           AbbeyGrange:Criminal   

                             what                          where  
0               CrookedMan:Murphy                        <bos_e>  
1               DevilsFoot:Case_1                DevilsFoot:Owen  
2               DancingMen:Cubitt         CrookedMan:living_room  
3   CrookedMan:key_of_living_room              CrookedMan:Murphy  
4         SilverBlaze:Silas_Brown          DancingMen:Abe_Slaney  
5             word.predicate:find       SilverBlaze:Silver_Blaze  
6           DancingMen:Abe_Slaney  AbbeyGrange:Lady_Brackenstall  
7                CrookedMan:beast     SpeckledBand:1883-04-01T15  
8                DancingMen:Elsie         ACaseOfIdentity:letter  
9   SilverBlaze:Inspector_Gregory       AbbeyGrange:Abbey_Grange  
10       SilverBlaze:Silver_Blaze           DevilsFoot:Sterndale  
11               CrookedMan:Henry              DevilsFoot:Case_1  
12       SilverBlaze:Edith_Baxter     ACaseOfIdentity:Sutherland  
13           word.predicate:teach            CrookedMan:Morrison  
14           word.predicate:think             CrookedMan:Barclay  
15         SilverBlaze:Ned_Hunter          word.predicate:return  
16              SilverBlaze:Horse                AllTitle:Holmes  
17          ACaseOfIdentity:money       

398

['CrookedMan:371', 'kgc:infoSource', 'AllTitle:Holmes']

head        relation                             tail  \
382  CrookedMan:368        kgc:what                   CrookedMan:372   
313  CrookedMan:355     kgc:subject                 CrookedMan:Teddy   
316  CrookedMan:355        kgc:when           CrookedMan:every_night   
379  CrookedMan:368        kgc:what                   CrookedMan:369   
318  CrookedMan:356     kgc:subject                 CrookedMan:Henry   
398  CrookedMan:371  kgc:infoSource                  AllTitle:Holmes   
367  CrookedMan:366  kgc:infoSource                CrookedMan:Murphy   
417        <mask_e>       kgc:where                         <mask_e>   
315  CrookedMan:355        kgc:what               CrookedMan:soldier   
392  CrookedMan:370  kgc:infoSource                  AllTitle:Holmes   
311  CrookedMan:353        kgc:when           CrookedMan:every_night   
322  CrookedMan:357     kgc:subject                CrookedMan:police   
365  CrookedMan:366     kgc:subject               CrookedMan:Barclay   
381  CrookedMan:368        kgc:what                   CrookedMan:371   
388  CrookedMan:369  kgc:infoSource                  AllTitle:Holmes   
415        <mask_e>         kgc:why                         <mask_e>   
411        <mask_e>  kgc:infoSource                  AllTitle:Holmes   
409  CrookedMan:373  kgc:infoSource                  AllTitle:Holmes   
283  CrookedMan:347  kgc:infoSource                  AllTitle:Holmes   
408  CrookedMan:373        kgc:what  CrookedMan:postscript_of_Samuel   

     atten_from398  
382       0.009764  
313       0.009204  
316       0.008996  
379       0.008850  
318       0.008820  
398       0.008723  
367       0.008675  
417       0.007880  
315       0.007843  
392       0.007766  
311       0.007589  
322       0.007373  
365       0.007143  
381       0.007056  
388       0.006828  
415       0.006740  
411       0.006632  
409       0.006444  
283       0.006299  
408       0.006181

----------


...

----------


417

['<mask_e>', 'kgc:where', '<mask_e>']

head        relation  \
322  CrookedMan:357     kgc:subject   
323  CrookedMan:357     kgc:subject   
318  CrookedMan:356     kgc:subject   
329  CrookedMan:359     kgc:subject   
313  CrookedMan:355     kgc:subject   
417        <mask_e>       kgc:where   
365  CrookedMan:366     kgc:subject   
390  CrookedMan:370     kgc:subject   
405  CrookedMan:373     kgc:subject   
382  CrookedMan:368        kgc:what   
395  CrookedMan:371     kgc:subject   
326  CrookedMan:358     kgc:subject   
387  CrookedMan:369       kgc:where   
379  CrookedMan:368        kgc:what   
394  CrookedMan:371     kgc:subject   
381  CrookedMan:368        kgc:what   
392  CrookedMan:370  kgc:infoSource   
414        <mask_e>     kgc:subject   
367  CrookedMan:366  kgc:infoSource   
385  CrookedMan:369     kgc:subject   

                                          tail  atten_from417  
322                          CrookedMan:police       0.030939  
323                           CrookedMan:Nancy       0.019801  
318                           CrookedMan:Henry       0.018286  
329                           CrookedMan:Henry       0.017384  
313                           CrookedMan:Teddy       0.017002  
417                                   <mask_e>       0.016380  
365                         CrookedMan:Barclay       0.016012  
390                          CrookedMan:Davide       0.014378  
405  CrookedMan:episode_of_Uriah_and_Bathsheba       0.012324  
382                             CrookedMan:372       0.012164  
395                         CrookedMan:Barclay       0.012107  
326                         CrookedMan:Barclay       0.011209  
387                   CrookedMan:Old_Testament       0.011185  
379                             CrookedMan:369       0.011018  
394                          CrookedMan:Davide       0.010443  
381                             CrookedMan:371       0.008505  
392                            AllTitle:Holmes       0.008445  
414                         CrookedMan:Barclay       0.008439  
367                          CrookedMan:Murphy       0.008384  
385                          CrookedMan:Davide       0.008154

----------


### 花嫁失踪事件（同一事件）
hozmaの失踪の名瀬を探る
被害者: ACaseOfIdentity:Hozma
犯人: 
犯行動機: 

In [26]:
victim = 'ACaseOfIdentity:Hosmer'
df_ranking_ACaseOfIdentity, df_attension_ACaseOfIdentity = make_ranking(
    'ACaseOfIdentity:510', 'ACaseOfIdentity:578', HIDE, victim, MASK_E, MASK_E, MASK_E, MASK_E)

display(df_ranking_ACaseOfIdentity.iloc[:20,:])
# display(df_attension_SpeckledBand)
# ヒートマップの作成
# sns.heatmap(df_atten.iloc[:,3:].iloc[:32,:32])
len_ = len(df_attension_ACaseOfIdentity)
for i in range(len_-20, len_):
    display(i, df_attension_ACaseOfIdentity.iloc[i,:3].tolist())
    display(df_attension_ACaseOfIdentity.sort_values(f'atten_from{i}', ascending=False).iloc[:20,[0,1,2,3+i]])
    print("----------")


predicate                                  whom  \
0     ACaseOfIdentity:Sutherland            ACaseOfIdentity:Sutherland   
1                AllTitle:Holmes                       AllTitle:Holmes   
2            word.predicate:kill                       AllTitle:Watson   
3             word.predicate:say                ACaseOfIdentity:Hosmer   
4           word.predicate:exist                               <bos_e>   
5            word.predicate:meet                   DevilsFoot:Mortimer   
6          word.predicate:inform           AbbeyGrange:Stanley_Hopkins   
7            word.predicate:find             ACaseOfIdentity:Windibank   
8      ACaseOfIdentity:Windibank  ACaseOfIdentity:mother_of_Sutherland   
9         word.predicate:suspect                     word.predicate:go   
10             word.predicate:go          SpeckledBand:Julia_s_bedroom   
11  SpeckledBand:Julia_s_bedroom                    word.predicate:say   
12         word.predicate:become         AbbeyGrange:Lady_Brackenstall   
13          word.predicate:visit                     DevilsFoot:Brenda   
14        ACaseOfIdentity:Hosmer               AbbeyGrange:Jack_Croker   
15           word.predicate:send                  SpeckledBand:Roylott   
16           word.predicate:know          DateTime:1883-04-02T04:00:00   
17            CrookedMan:Barclay                   word.predicate:find   
18          word.predicate:think                       DevilsFoot:Owen   
19         word.predicate:return                CrookedMan:living_room   

                                 subject  \
0             ACaseOfIdentity:Sutherland   
1                        AllTitle:Holmes   
2              ACaseOfIdentity:Windibank   
3                        AllTitle:Watson   
4   ACaseOfIdentity:mother_of_Sutherland   
5           SpeckledBand:Julia_s_bedroom   
6                 ACaseOfIdentity:Hosmer   
7                   SpeckledBand:coroner   
8     ACaseOfIdentity:Hosmer_s_statement   
9                    DevilsFoot:Mortimer   
10           AbbeyGrange:Stanley_Hopkins   
11                     word.predicate:go   
12                    AbbeyGrange:police   
13                       DevilsFoot:Owen   
14                   word.predicate:find   
15                               <bos_e>   
16                    word.predicate:say   
17               AbbeyGrange:Jack_Croker   
18                     DevilsFoot:Brenda   
19                  SpeckledBand:Roylott   

                                             why  \
0                     ACaseOfIdentity:Sutherland   
1                   SpeckledBand:Julia_s_bedroom   
2                                AllTitle:Holmes   
3                      ACaseOfIdentity:Windibank   
4                        AbbeyGrange:Jack_Croker   
5                                AllTitle:Watson   
6                            AbbeyGrange:bracket   
7                              DevilsFoot:Brenda   
8                            word.predicate:wear   
9                             AbbeyGrange:police   
10                           CrookedMan:Thursday   
11                               DevilsFoot:Owen   
12         ACaseOfIdentity:Sutherland_s_thoughts   
13                   AbbeyGrange:Stanley_Hopkins   
14                        AbbeyGrange:appearance   
15                 AbbeyGrange:Lady_Brackenstall   
16                        word.predicate:confirm   
17                      CrookedMan:Royal_Mallows   
18                          SpeckledBand:coroner   
19  ACaseOfIdentity:shop_of_father_of_Sutherland   

                                    what  \
0             ACaseOfIdentity:Sutherland   
1                        AllTitle:Holmes   
2                        AllTitle:Watson   
3              ACaseOfIdentity:Windibank   
4                AbbeyGrange:Jack_Croker   
5   ACaseOfIdentity:mother_of_Sutherland   
6           SpeckledBand:Julia_s_bedroom   
7                      word.predicate:go   
8                        DevilsFoot:room   
9         

356

['ACaseOfIdentity:576', 'kgc:what', 'ACaseOfIdentity:577']

head        relation                                tail  \
273  ACaseOfIdentity:560     kgc:subject           ACaseOfIdentity:Windibank   
268  ACaseOfIdentity:559     kgc:subject           ACaseOfIdentity:Windibank   
169  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:547   
166  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:544   
284  ACaseOfIdentity:562     kgc:subject           ACaseOfIdentity:Windibank   
362  ACaseOfIdentity:577  kgc:infoSource  ACaseOfIdentity:someone_of_Company   
167  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:545   
241  ACaseOfIdentity:557     kgc:subject           ACaseOfIdentity:Windibank   
271  ACaseOfIdentity:559  kgc:infoSource                     AllTitle:Holmes   
266  ACaseOfIdentity:558        kgc:what                 ACaseOfIdentity:580   
364  ACaseOfIdentity:578     kgc:subject          ACaseOfIdentity:Sutherland   
171  ACaseOfIdentity:542     kgc:subject           ACaseOfIdentity:Windibank   
305  ACaseOfIdentity:566     kgc:subject          ACaseOfIdentity:Sutherland   
244  ACaseOfIdentity:558     kgc:subject                     AllTitle:Holmes   
287  ACaseOfIdentity:562  kgc:infoSource                     AllTitle:Holmes   
331  ACaseOfIdentity:571       kgc:where             ACaseOfIdentity:Company   
252  ACaseOfIdentity:558        kgc:what                 ACaseOfIdentity:565   
310  ACaseOfIdentity:568     kgc:subject          ACaseOfIdentity:Sutherland   
263  ACaseOfIdentity:558        kgc:what                 ACaseOfIdentity:576   
254  ACaseOfIdentity:558        kgc:what                 ACaseOfIdentity:567   

     atten_from356  
273       0.026379  
268       0.018113  
169       0.010694  
166       0.010604  
284       0.009344  
362       0.008929  
167       0.008446  
241       0.008292  
271       0.008237  
266       0.007948  
364       0.007722  
171       0.007717  
305       0.007583  
244       0.007532  
287       0.007363  
331       0.007337  
252       0.007260  
310       0.007242  
263       0.006931  
254       0.006925

----------


...

----------


375

['<mask_e>', 'kgc:where', '<mask_e>']

head        relation                                tail  \
273  ACaseOfIdentity:560     kgc:subject           ACaseOfIdentity:Windibank   
364  ACaseOfIdentity:578     kgc:subject          ACaseOfIdentity:Sutherland   
305  ACaseOfIdentity:566     kgc:subject          ACaseOfIdentity:Sutherland   
289  ACaseOfIdentity:563     kgc:subject           ACaseOfIdentity:Windibank   
268  ACaseOfIdentity:559     kgc:subject           ACaseOfIdentity:Windibank   
349  ACaseOfIdentity:575     kgc:subject     ACaseOfIdentity:feature_of_type   
362  ACaseOfIdentity:577  kgc:infoSource  ACaseOfIdentity:someone_of_Company   
290  ACaseOfIdentity:563     kgc:subject              ACaseOfIdentity:Hosmer   
375             <mask_e>       kgc:where                            <mask_e>   
310  ACaseOfIdentity:568     kgc:subject          ACaseOfIdentity:Sutherland   
345  ACaseOfIdentity:574     kgc:subject               ACaseOfIdentity:reply   
359  ACaseOfIdentity:577     kgc:subject  ACaseOfIdentity:Personal_statement   
284  ACaseOfIdentity:562     kgc:subject           ACaseOfIdentity:Windibank   
372             <mask_e>     kgc:subject                            <mask_e>   
361  ACaseOfIdentity:577        kgc:what           ACaseOfIdentity:Windibank   
369             <mask_e>  kgc:infoSource                     AllTitle:Holmes   
331  ACaseOfIdentity:571       kgc:where             ACaseOfIdentity:Company   
241  ACaseOfIdentity:557     kgc:subject           ACaseOfIdentity:Windibank   
169  ACaseOfIdentity:541        kgc:what                 ACaseOfIdentity:547   
366  ACaseOfIdentity:578        kgc:what                     AllTitle:Holmes   

     atten_from375  
273       0.037948  
364       0.016977  
305       0.013334  
289       0.012335  
268       0.012037  
349       0.011685  
362       0.011676  
290       0.011227  
375       0.011084  
310       0.011044  
345       0.010106  
359       0.010062  
284       0.009935  
372       0.009093  
361       0.009073  
369       0.009050  
331       0.008818  
241       0.008505  
169       0.008028  
366       0.007610

----------
